In [1]:
import pandas as pd
import numpy as np
import re
import datetime
import time
from os import cpu_count
from collections import defaultdict

from sklearn.preprocessing import LabelEncoder
from sklearn.model_selection import cross_val_score, GridSearchCV, StratifiedKFold, train_test_split
from sklearn.metrics import mean_absolute_error
import lightgbm as lgb

In [2]:
pd.options.display.max_columns = None
pd.options.display.max_rows = 50
n_jobs = max(cpu_count()-1, 1)

In [3]:
train = pd.read_csv("D:/Job/interview/datascientist-master/train_ds.csv")
test = pd.read_csv("D:/Job/interview/datascientist-master/test_ds.csv")

In [4]:
train.head()

cgsettlementbufferid   mcc  tranccy  ccy  amount  \
0                     1  4131      978  980    6730   
1                     2  5651      978  980   55912   
2                     3  5812      978  980  135658   
3                     4  5947      978  980  138294   
4                     5  5651      978  980  426209   

                                   location  trandatetime  sexid  clientid  
0  TRAMBESOS              SANT JOAN DES  ES    1385977762      1        13  
1  ZARA BARCELONA P GRACIABARCELONA      ES    1385991764      1        13  
2  CAFE DE L'ACADEMIA     BARCELONA      ES    1385999148      1        13  
3  2D BCN DISSENY EN BIJUTBARCELONA      ES    1385999979      1        13  
4  EL GANSO               BARCELONA      ES    1386005648      1        13

In [5]:
test.head()

cgsettlementbufferid   mcc  tranccy  ccy  amount  \
0                   395  5411      980  980    7488   
1                   422  6010      980  980   40000   
2                   429  6010      980  980  119000   
3                   435  6010      980  980  210000   
4                   445  6011      980  980   30000   

                                   location  trandatetime  clientid  
0  VOPAK 7301             UZHGOROD       UA    1393172737       712  
1  ODESA REGIONAL DEP.    ODESSA         UA    1393509649       766  
2  ODESA REGIONAL DEP.    ODESSA         UA    1393583520       745  
3  ODESA REGIONAL DEP.    ODESSA         UA    1393591808       748  
4  GAGARINA, 13           ODESSA         UA    1393766754       766

In [6]:
train.info()

<class 'pandas.core.frame.DataFrame'>
RangeIndex: 92700 entries, 0 to 92699
Data columns (total 9 columns):
cgsettlementbufferid    92700 non-null int64
mcc                     92700 non-null int64
tranccy                 92700 non-null int64
ccy                     92700 non-null int64
amount                  92700 non-null int64
location                92700 non-null object
trandatetime            92700 non-null int64
sexid                   92700 non-null int64
clientid                92700 non-null int64
dtypes: int64(8), object(1)
memory usage: 6.4+ MB


In [7]:
train_location = train.location
test_location = test.location

In [8]:
train_location.head()

0    TRAMBESOS              SANT JOAN DES  ES
1    ZARA BARCELONA P GRACIABARCELONA      ES
2    CAFE DE L'ACADEMIA     BARCELONA      ES
3    2D BCN DISSENY EN BIJUTBARCELONA      ES
4    EL GANSO               BARCELONA      ES
Name: location, dtype: object

In [9]:
test_location.head()

0    VOPAK 7301             UZHGOROD       UA
1    ODESA REGIONAL DEP.    ODESSA         UA
2    ODESA REGIONAL DEP.    ODESSA         UA
3    ODESA REGIONAL DEP.    ODESSA         UA
4    GAGARINA, 13           ODESSA         UA
Name: location, dtype: object

In [10]:
test_df = test.copy() 
train_df = train.copy()

In [11]:
institution_transaction_train = list()
city_transaction_train  = list()
country_transaction_train  = list()
institution_transaction_test = list()
city_transaction_test = list()
country_transaction_test = list()

In [12]:
for i in range(0,train_location.size):
    institution_transaction_train.append(train_location[i][0:23])
    city_transaction_train.append(train_location[i][23:38])
    country_transaction_train.append(train_location[i][38:])

In [13]:
for i in range(0,test_location.size):
    institution_transaction_test.append(test_location[i][0:23])
    city_transaction_test.append(test_location[i][23:38])
    country_transaction_test.append(test_location[i][38:])

In [14]:
del_tabs = lambda x: re.sub(r"\s+", " ", x).rstrip('\t\n ')

In [15]:
institution_transaction_train = pd.DataFrame(institution_transaction_train)[0].apply(del_tabs)
city_transaction_train = pd.DataFrame(city_transaction_train)[0].apply(del_tabs)
country_transaction_train = pd.DataFrame(country_transaction_train)[0].apply(del_tabs)

institution_transaction_test = pd.DataFrame(institution_transaction_test)[0].apply(del_tabs)
city_transaction_test = pd.DataFrame(city_transaction_test)[0].apply(del_tabs)
country_transaction_test = pd.DataFrame(country_transaction_test)[0].apply(del_tabs)

In [16]:
train_df["institution_transaction"] = institution_transaction_train
train_df["city_transaction"] = city_transaction_train
train_df["country_transaction"] = country_transaction_train

In [17]:
test_df["institution_transaction"] = institution_transaction_test
test_df["city_transaction"] = city_transaction_test
test_df["country_transaction"] = country_transaction_test

In [18]:
train_df.head()

cgsettlementbufferid   mcc  tranccy  ccy  amount  \
0                     1  4131      978  980    6730   
1                     2  5651      978  980   55912   
2                     3  5812      978  980  135658   
3                     4  5947      978  980  138294   
4                     5  5651      978  980  426209   

                                   location  trandatetime  sexid  clientid  \
0  TRAMBESOS              SANT JOAN DES  ES    1385977762      1        13   
1  ZARA BARCELONA P GRACIABARCELONA      ES    1385991764      1        13   
2  CAFE DE L'ACADEMIA     BARCELONA      ES    1385999148      1        13   
3  2D BCN DISSENY EN BIJUTBARCELONA      ES    1385999979      1        13   
4  EL GANSO               BARCELONA      ES    1386005648      1        13   

   institution_transaction city_transaction country_transaction  
0                TRAMBESOS    SANT JOAN DES                  ES  
1  ZARA BARCELONA P GRACIA        BARCELONA                  ES  
2       CAFE DE L'ACADEMIA        BARCELONA                  ES  
3  2D BCN DISSENY EN BIJUT        BARCELONA                  ES  
4                 EL GANSO        BARCELONA                  ES

In [19]:
train_df.tail()

cgsettlementbufferid   mcc  tranccy  ccy  amount  \
92695                147546  5499      980  980   12870   
92696                147547  5499      980  980   11529   
92697                147550  5499      980  980    2379   
92698                147554  5499      980  980    4650   
92699                147555  5541      980  980   50017   

                                       location  trandatetime  sexid  \
92695  PR305                  ZAPOROZHYE   UAUA    1437413456      1   
92696  2SHAGAJUKOVA           ODESSA       UAUA    1437413573      0   
92697  B09                    LVOV         UAUA    1437413997      1   
92698  magazin1189            Brovari      UAUA    1437414625      1   
92699  PREMIERLIGA26          KIYEV        UAUA    1437414806      0   

       clientid institution_transaction city_transaction country_transaction  
92695      9378                   PR305    ZAPOROZHYE UA                  UA  
92696      3533            2SHAGAJUKOVA        ODESSA UA                  UA  
92697      7745                     B09          LVOV UA                  UA  
92698      7287             magazin1189       Brovari UA                  UA  
92699      9001           PREMIERLIGA26         KIYEV UA                  UA

In [20]:
test_df.head()

cgsettlementbufferid   mcc  tranccy  ccy  amount  \
0                   395  5411      980  980    7488   
1                   422  6010      980  980   40000   
2                   429  6010      980  980  119000   
3                   435  6010      980  980  210000   
4                   445  6011      980  980   30000   

                                   location  trandatetime  clientid  \
0  VOPAK 7301             UZHGOROD       UA    1393172737       712   
1  ODESA REGIONAL DEP.    ODESSA         UA    1393509649       766   
2  ODESA REGIONAL DEP.    ODESSA         UA    1393583520       745   
3  ODESA REGIONAL DEP.    ODESSA         UA    1393591808       748   
4  GAGARINA, 13           ODESSA         UA    1393766754       766   

  institution_transaction city_transaction country_transaction  
0              VOPAK 7301         UZHGOROD                  UA  
1     ODESA REGIONAL DEP.           ODESSA                  UA  
2     ODESA REGIONAL DEP.           ODESSA                  UA  
3     ODESA REGIONAL DEP.           ODESSA                  UA  
4            GAGARINA, 13           ODESSA                  UA

In [21]:
test_df.tail()

cgsettlementbufferid   mcc  tranccy  ccy  amount  \
40554                147548  5499      980  980   21185   
40555                147549  5411      980  980   49453   
40556                147551  6538      980  980  300000   
40557                147552  5977      980  980   31400   
40558                147553  5499      980  980    2257   

                                       location  trandatetime  clientid  \
40554  PR305                  ZAPOROZHYE   UAUA    1437413578      9382   
40555  TMETRO16               KIYEV        UAUA    1437413600      2136   
40556  MFPay2youAC            Kiiev        UAUA    1437414144      7145   
40557  LUSH ODESSA            ODESSA       UAUA    1437414216      1076   
40558  OD019                  ODESSA       UAUA    1437414269      1582   

      institution_transaction city_transaction country_transaction  
40554                   PR305    ZAPOROZHYE UA                  UA  
40555                TMETRO16         KIYEV UA                  UA  
40556             MFPay2youAC         Kiiev UA                  UA  
40557             LUSH ODESSA        ODESSA UA                  UA  
40558                   OD019        ODESSA UA                  UA

# Task A

In [22]:
train_df_A = train_df.copy()
test_df_A = test_df.copy()

In [23]:
#train_df_A.drop(["location","city_transaction","country_transaction"],axis=1,inplace=True)
#test_df_A.drop(["location","city_transaction","country_transaction"],axis=1,inplace=True)
train_df_A.drop(["location"],axis=1,inplace=True)
test_df_A.drop(["location"],axis=1,inplace=True)

In [24]:
train_df_A.info()

<class 'pandas.core.frame.DataFrame'>
RangeIndex: 92700 entries, 0 to 92699
Data columns (total 11 columns):
cgsettlementbufferid       92700 non-null int64
mcc                        92700 non-null int64
tranccy                    92700 non-null int64
ccy                        92700 non-null int64
amount                     92700 non-null int64
trandatetime               92700 non-null int64
sexid                      92700 non-null int64
clientid                   92700 non-null int64
institution_transaction    92700 non-null object
city_transaction           92700 non-null object
country_transaction        92700 non-null object
dtypes: int64(8), object(3)
memory usage: 7.8+ MB


In [25]:
test_df_A.info()

<class 'pandas.core.frame.DataFrame'>
RangeIndex: 40559 entries, 0 to 40558
Data columns (total 10 columns):
cgsettlementbufferid       40559 non-null int64
mcc                        40559 non-null int64
tranccy                    40559 non-null int64
ccy                        40559 non-null int64
amount                     40559 non-null int64
trandatetime               40559 non-null int64
clientid                   40559 non-null int64
institution_transaction    40559 non-null object
city_transaction           40559 non-null object
country_transaction        40559 non-null object
dtypes: int64(7), object(3)
memory usage: 3.1+ MB


#to_timespan = (lambda x: time.mktime(x.timetuple()))

#train_df_A["trandatetime"] = train_df_A["trandatetime"].apply(to_timespan).astype(np.int64)

In [27]:
categorical = [
    'institution_transaction',
    'city_transaction',
    'country_transaction'
]

In [28]:
#from collections import defaultdict
#from sklearn.preprocessing import LabelEncoder

def __encode_categorical(df_list, cat_cols):
    # initialize placeholder
    d = defaultdict(LabelEncoder)
    # fit and encode train/test,
    codes = pd.concat(
        [df[cat_cols] for df in df_list],
        axis=0
    ).fillna('').apply(
        lambda x: d[x.name].fit(x)
    ),
    # transform encodings to train/test etc
    for df in df_list:
        df[cat_cols] = df[cat_cols].fillna('').apply(
            lambda x: d[x.name].transform(x))

__encode_categorical(df_list=[train_df_A, test_df_A], cat_cols=categorical) 

In [29]:
train_df_A.head()

cgsettlementbufferid   mcc  tranccy  ccy  amount  trandatetime  sexid  \
0                     1  4131      978  980    6730    1385977762      1   
1                     2  5651      978  980   55912    1385991764      1   
2                     3  5812      978  980  135658    1385999148      1   
3                     4  5947      978  980  138294    1385999979      1   
4                     5  5651      978  980  426209    1386005648      1   

   clientid  institution_transaction  city_transaction  country_transaction  
0        13                    20316              2754                   30  
1        13                    22254               422                   30  
2        13                     5443               422                   30  
3        13                      653               422                   30  
4        13                     8015               422                   30

In [30]:
test_df_A.head()

cgsettlementbufferid   mcc  tranccy  ccy  amount  trandatetime  clientid  \
0                   395  5411      980  980    7488    1393172737       712   
1                   422  6010      980  980   40000    1393509649       766   
2                   429  6010      980  980  119000    1393583520       745   
3                   435  6010      980  980  210000    1393591808       748   
4                   445  6011      980  980   30000    1393766754       766   

   institution_transaction  city_transaction  country_transaction  
0                    21650              3198                   87  
1                    14491              2247                   87  
2                    14491              2247                   87  
3                    14491              2247                   87  
4                     9353              2247                   87

# Validation

In [31]:
X = train_df_A.drop(['sexid'], axis=1)
y = train_df_A['sexid']

In [32]:
skf = StratifiedKFold(n_splits=5, shuffle=True, random_state=42)

In [33]:
parameters={
   'objective': 'binary',
    'learning_rate': 0.01,
    'max_depth': 8,
    'num_threads': 4,
    'metric': 'mae',
    'seed': 42,
    'colsample_bytree': 0.9,
    'subsample': 0.9,
    'subsample_freq': 2,
    'min_data_in_leaf': 15,
}
n_rounds = 20000

In [34]:
(100/(train_df_A.shape[0]+test_df_A.shape[0]))*40559

30.43621819164184

In [35]:
X_train, X_val, y_train, y_val = train_test_split(X, y, test_size=0.304, random_state=42)

In [36]:
lgb_train = lgb.Dataset(X_train, label=y_train, free_raw_data=False)

In [37]:
lgd_classifier = lgb.cv(parameters, lgb_train, n_rounds, folds=skf.split(X_train, y_train), early_stopping_rounds=10, verbose_eval=1, )

[1]	cv_agg's l1: 0.498846 + 2.50491e-05
[2]	cv_agg's l1: 0.497694 + 3.86026e-05
[3]	cv_agg's l1: 0.496558 + 3.19498e-05
[4]	cv_agg's l1: 0.49543 + 4.67302e-05
[5]	cv_agg's l1: 0.494142 + 4.6937e-05
[6]	cv_agg's l1: 0.493031 + 5.73766e-05
[7]	cv_agg's l1: 0.491939 + 7.54259e-05
[8]	cv_agg's l1: 0.49074 + 7.55162e-05
[9]	cv_agg's l1: 0.489655 + 0.000105455
[10]	cv_agg's l1: 0.489219 + 0.000108827
[11]	cv_agg's l1: 0.488125 + 0.000151793
[12]	cv_agg's l1: 0.487045 + 0.000187498
[13]	cv_agg's l1: 0.486018 + 0.000193343
[14]	cv_agg's l1: 0.484868 + 0.000193753
[15]	cv_agg's l1: 0.483828 + 0.000199761
[16]	cv_agg's l1: 0.48339 + 0.000196544
[17]	cv_agg's l1: 0.482377 + 0.000223242
[18]	cv_agg's l1: 0.481352 + 0.000241812
[19]	cv_agg's l1: 0.48036 + 0.000282524
[20]	cv_agg's l1: 0.479405 + 0.000288329
[21]	cv_agg's l1: 0.478417 + 0.000291723
[22]	cv_agg's l1: 0.477448 + 0.000283489
[23]	cv_agg's l1: 0.47639 + 0.000265875
[24]	cv_agg's l1: 0.475425 + 0.000286881
[25]	cv_agg's l1: 0.474468 + 0.

[204]	cv_agg's l1: 0.382528 + 0.00142728
[205]	cv_agg's l1: 0.382239 + 0.00146846
[206]	cv_agg's l1: 0.381981 + 0.0014897
[207]	cv_agg's l1: 0.381815 + 0.00148956
[208]	cv_agg's l1: 0.381539 + 0.00144687
[209]	cv_agg's l1: 0.381292 + 0.00143569
[210]	cv_agg's l1: 0.381018 + 0.00140828
[211]	cv_agg's l1: 0.380803 + 0.0013689
[212]	cv_agg's l1: 0.380607 + 0.00132979
[213]	cv_agg's l1: 0.380451 + 0.00134042
[214]	cv_agg's l1: 0.38014 + 0.00138744
[215]	cv_agg's l1: 0.379847 + 0.00139822
[216]	cv_agg's l1: 0.379575 + 0.00140968
[217]	cv_agg's l1: 0.379314 + 0.00138243
[218]	cv_agg's l1: 0.379139 + 0.00138259
[219]	cv_agg's l1: 0.378987 + 0.00138838
[220]	cv_agg's l1: 0.378701 + 0.00134705
[221]	cv_agg's l1: 0.378421 + 0.00130147
[222]	cv_agg's l1: 0.378091 + 0.00126992
[223]	cv_agg's l1: 0.377927 + 0.00127068
[224]	cv_agg's l1: 0.377678 + 0.00127837
[225]	cv_agg's l1: 0.377408 + 0.00128094
[226]	cv_agg's l1: 0.377079 + 0.00124217
[227]	cv_agg's l1: 0.37681 + 0.00127909
[228]	cv_agg's l1: 0

[406]	cv_agg's l1: 0.341793 + 0.00183597
[407]	cv_agg's l1: 0.341653 + 0.0018824
[408]	cv_agg's l1: 0.341496 + 0.00193089
[409]	cv_agg's l1: 0.341306 + 0.00192831
[410]	cv_agg's l1: 0.34114 + 0.00195582
[411]	cv_agg's l1: 0.340954 + 0.00196011
[412]	cv_agg's l1: 0.34078 + 0.00193007
[413]	cv_agg's l1: 0.340593 + 0.00193608
[414]	cv_agg's l1: 0.340426 + 0.00195385
[415]	cv_agg's l1: 0.34027 + 0.00197285
[416]	cv_agg's l1: 0.340109 + 0.00202123
[417]	cv_agg's l1: 0.339991 + 0.0019961
[418]	cv_agg's l1: 0.339882 + 0.00198654
[419]	cv_agg's l1: 0.339707 + 0.00201966
[420]	cv_agg's l1: 0.339549 + 0.00198727
[421]	cv_agg's l1: 0.339377 + 0.00201035
[422]	cv_agg's l1: 0.339199 + 0.0020311
[423]	cv_agg's l1: 0.339047 + 0.00208053
[424]	cv_agg's l1: 0.338893 + 0.00212711
[425]	cv_agg's l1: 0.338741 + 0.00207235
[426]	cv_agg's l1: 0.338572 + 0.0020703
[427]	cv_agg's l1: 0.338443 + 0.00206218
[428]	cv_agg's l1: 0.338323 + 0.00206572
[429]	cv_agg's l1: 0.338126 + 0.00202368
[430]	cv_agg's l1: 0.33

[612]	cv_agg's l1: 0.313917 + 0.000772135
[613]	cv_agg's l1: 0.313809 + 0.000793533
[614]	cv_agg's l1: 0.313671 + 0.000874679
[615]	cv_agg's l1: 0.313551 + 0.00083796
[616]	cv_agg's l1: 0.31346 + 0.00086072
[617]	cv_agg's l1: 0.313344 + 0.000914505
[618]	cv_agg's l1: 0.313216 + 0.00096487
[619]	cv_agg's l1: 0.313112 + 0.00093833
[620]	cv_agg's l1: 0.312996 + 0.000924988
[621]	cv_agg's l1: 0.312904 + 0.00093078
[622]	cv_agg's l1: 0.312804 + 0.000937522
[623]	cv_agg's l1: 0.312729 + 0.000931338
[624]	cv_agg's l1: 0.312657 + 0.00092648
[625]	cv_agg's l1: 0.312587 + 0.000908765
[626]	cv_agg's l1: 0.312492 + 0.000920698
[627]	cv_agg's l1: 0.312407 + 0.000920028
[628]	cv_agg's l1: 0.312315 + 0.000932624
[629]	cv_agg's l1: 0.312164 + 0.00091982
[630]	cv_agg's l1: 0.312014 + 0.000912642
[631]	cv_agg's l1: 0.311882 + 0.000892839
[632]	cv_agg's l1: 0.311756 + 0.000867192
[633]	cv_agg's l1: 0.311644 + 0.000900542
[634]	cv_agg's l1: 0.311552 + 0.000901902
[635]	cv_agg's l1: 0.311424 + 0.000858436


[817]	cv_agg's l1: 0.293155 + 0.000829137
[818]	cv_agg's l1: 0.293054 + 0.000818063
[819]	cv_agg's l1: 0.292923 + 0.000802527
[820]	cv_agg's l1: 0.292853 + 0.000791743
[821]	cv_agg's l1: 0.292742 + 0.000745383
[822]	cv_agg's l1: 0.292638 + 0.000698417
[823]	cv_agg's l1: 0.292601 + 0.00070082
[824]	cv_agg's l1: 0.292486 + 0.000719462
[825]	cv_agg's l1: 0.292413 + 0.000707742
[826]	cv_agg's l1: 0.292353 + 0.000687426
[827]	cv_agg's l1: 0.292281 + 0.000658996
[828]	cv_agg's l1: 0.292174 + 0.000608756
[829]	cv_agg's l1: 0.292071 + 0.000624469
[830]	cv_agg's l1: 0.291971 + 0.000642227
[831]	cv_agg's l1: 0.291856 + 0.000642431
[832]	cv_agg's l1: 0.291727 + 0.000664298
[833]	cv_agg's l1: 0.291642 + 0.000665973
[834]	cv_agg's l1: 0.291551 + 0.00067737
[835]	cv_agg's l1: 0.291432 + 0.000689594
[836]	cv_agg's l1: 0.291318 + 0.000708762
[837]	cv_agg's l1: 0.291223 + 0.000680555
[838]	cv_agg's l1: 0.291119 + 0.000649209
[839]	cv_agg's l1: 0.291042 + 0.000629714
[840]	cv_agg's l1: 0.29095 + 0.00062

...

[19091]	cv_agg's l1: 0.106268 + 0.00215001
[19092]	cv_agg's l1: 0.106266 + 0.00215251
[19093]	cv_agg's l1: 0.106264 + 0.0021525
[19094]	cv_agg's l1: 0.106262 + 0.00215209
[19095]	cv_agg's l1: 0.106259 + 0.0021518
[19096]	cv_agg's l1: 0.106256 + 0.00215102
[19097]	cv_agg's l1: 0.106254 + 0.00214981
[19098]	cv_agg's l1: 0.106253 + 0.00214855
[19099]	cv_agg's l1: 0.10625 + 0.00214965
[19100]	cv_agg's l1: 0.106249 + 0.00215121
[19101]	cv_agg's l1: 0.106245 + 0.00215012
[19102]	cv_agg's l1: 0.106242 + 0.00214909
[19103]	cv_agg's l1: 0.106241 + 0.00215057
[19104]	cv_agg's l1: 0.10624 + 0.00215184
[19105]	cv_agg's l1: 0.106238 + 0.00215235
[19106]	cv_agg's l1: 0.106237 + 0.0021527
[19107]	cv_agg's l1: 0.106235 + 0.00215543
[19108]	cv_agg's l1: 0.106233 + 0.00215608
[19109]	cv_agg's l1: 0.106232 + 0.00215578
[19110]	cv_agg's l1: 0.106231 + 0.00215653
[19111]	cv_agg's l1: 0.106228 + 0.00215807
[19112]	cv_agg's l1: 0.106226 + 0.0021596
[19113]	cv_agg's l1: 0.106224 + 0.00215982
[19114]	cv_agg's 

[19284]	cv_agg's l1: 0.105903 + 0.00215543
[19285]	cv_agg's l1: 0.105903 + 0.00215559
[19286]	cv_agg's l1: 0.1059 + 0.00215492
[19287]	cv_agg's l1: 0.105898 + 0.00215491
[19288]	cv_agg's l1: 0.105898 + 0.00215456
[19289]	cv_agg's l1: 0.105897 + 0.00215425
[19290]	cv_agg's l1: 0.105894 + 0.0021545
[19291]	cv_agg's l1: 0.105891 + 0.00215321
[19292]	cv_agg's l1: 0.105888 + 0.00215162
[19293]	cv_agg's l1: 0.105886 + 0.00215236
[19294]	cv_agg's l1: 0.105884 + 0.00215132
[19295]	cv_agg's l1: 0.105879 + 0.00215248
[19296]	cv_agg's l1: 0.105876 + 0.00215272
[19297]	cv_agg's l1: 0.105875 + 0.00215262
[19298]	cv_agg's l1: 0.105872 + 0.002154
[19299]	cv_agg's l1: 0.105871 + 0.00215303
[19300]	cv_agg's l1: 0.10587 + 0.00215212
[19301]	cv_agg's l1: 0.10587 + 0.00215207
[19302]	cv_agg's l1: 0.10587 + 0.0021513
[19303]	cv_agg's l1: 0.105868 + 0.00215162
[19304]	cv_agg's l1: 0.105867 + 0.00215167
[19305]	cv_agg's l1: 0.105865 + 0.00215257
[19306]	cv_agg's l1: 0.105864 + 0.00215419
[19307]	cv_agg's l1:

[19483]	cv_agg's l1: 0.105521 + 0.00213473
[19484]	cv_agg's l1: 0.105518 + 0.00213205
[19485]	cv_agg's l1: 0.105516 + 0.00213169
[19486]	cv_agg's l1: 0.105515 + 0.00213174
[19487]	cv_agg's l1: 0.105513 + 0.00213151
[19488]	cv_agg's l1: 0.105511 + 0.0021313
[19489]	cv_agg's l1: 0.105509 + 0.00213234
[19490]	cv_agg's l1: 0.105507 + 0.00213396
[19491]	cv_agg's l1: 0.105505 + 0.00213425
[19492]	cv_agg's l1: 0.105502 + 0.00213505
[19493]	cv_agg's l1: 0.105501 + 0.00213512
[19494]	cv_agg's l1: 0.105499 + 0.00213508
[19495]	cv_agg's l1: 0.105497 + 0.00213483
[19496]	cv_agg's l1: 0.105496 + 0.00213362
[19497]	cv_agg's l1: 0.105496 + 0.00213348
[19498]	cv_agg's l1: 0.105494 + 0.00213245
[19499]	cv_agg's l1: 0.105492 + 0.0021305
[19500]	cv_agg's l1: 0.105489 + 0.00212974
[19501]	cv_agg's l1: 0.105487 + 0.00212953
[19502]	cv_agg's l1: 0.105485 + 0.00212913
[19503]	cv_agg's l1: 0.105484 + 0.00212896
[19504]	cv_agg's l1: 0.105484 + 0.0021289
[19505]	cv_agg's l1: 0.105481 + 0.00212909
[19506]	cv_agg

[19682]	cv_agg's l1: 0.105156 + 0.00212457
[19683]	cv_agg's l1: 0.105156 + 0.00212488
[19684]	cv_agg's l1: 0.105154 + 0.00212498
[19685]	cv_agg's l1: 0.105151 + 0.00212646
[19686]	cv_agg's l1: 0.105148 + 0.00212787
[19687]	cv_agg's l1: 0.105147 + 0.00212809
[19688]	cv_agg's l1: 0.105147 + 0.00212786
[19689]	cv_agg's l1: 0.105146 + 0.00212766
[19690]	cv_agg's l1: 0.105145 + 0.00212728
[19691]	cv_agg's l1: 0.105144 + 0.00212719
[19692]	cv_agg's l1: 0.105141 + 0.00212477
[19693]	cv_agg's l1: 0.105137 + 0.00212531
[19694]	cv_agg's l1: 0.105133 + 0.00212605
[19695]	cv_agg's l1: 0.105132 + 0.0021257
[19696]	cv_agg's l1: 0.105131 + 0.00212637
[19697]	cv_agg's l1: 0.105129 + 0.00212639
[19698]	cv_agg's l1: 0.105128 + 0.00212596
[19699]	cv_agg's l1: 0.105127 + 0.00212647
[19700]	cv_agg's l1: 0.105125 + 0.00212762
[19701]	cv_agg's l1: 0.105123 + 0.00212901
[19702]	cv_agg's l1: 0.105121 + 0.00213014
[19703]	cv_agg's l1: 0.105119 + 0.00213075
[19704]	cv_agg's l1: 0.105117 + 0.00213147
[19705]	cv_a

[19874]	cv_agg's l1: 0.10479 + 0.00215264
[19875]	cv_agg's l1: 0.104788 + 0.00215259
[19876]	cv_agg's l1: 0.104786 + 0.00215282
[19877]	cv_agg's l1: 0.104783 + 0.00215241
[19878]	cv_agg's l1: 0.104782 + 0.00215307
[19879]	cv_agg's l1: 0.10478 + 0.00215346
[19880]	cv_agg's l1: 0.104778 + 0.00215344
[19881]	cv_agg's l1: 0.104777 + 0.00215322
[19882]	cv_agg's l1: 0.104773 + 0.00215384
[19883]	cv_agg's l1: 0.104769 + 0.00215328
[19884]	cv_agg's l1: 0.104768 + 0.00215191
[19885]	cv_agg's l1: 0.104764 + 0.00214935
[19886]	cv_agg's l1: 0.104761 + 0.00214763
[19887]	cv_agg's l1: 0.10476 + 0.00214797
[19888]	cv_agg's l1: 0.104758 + 0.00214775
[19889]	cv_agg's l1: 0.104756 + 0.00214785
[19890]	cv_agg's l1: 0.104755 + 0.00214754
[19891]	cv_agg's l1: 0.104752 + 0.00214677
[19892]	cv_agg's l1: 0.104749 + 0.00214633
[19893]	cv_agg's l1: 0.104748 + 0.00214634
[19894]	cv_agg's l1: 0.104746 + 0.0021471
[19895]	cv_agg's l1: 0.104745 + 0.00214647
[19896]	cv_agg's l1: 0.104742 + 0.00214559
[19897]	cv_agg'

In [38]:
print(min(lgd_classifier['l1-mean']), len(lgd_classifier['l1-mean']))

0.10453544178179294 20000


In [39]:
bst = lgb.train(parameters, lgb_train,n_rounds)

In [40]:
predict_lgb = bst.predict(X_val,num_iteration=bst.best_iteration)

In [41]:
mean_absolute_error(y_val,predict_lgb)

0.09836847476008048

# Prediction

In [42]:
X_train = train_df_A.drop("sexid",axis=1)
y_train = train_df_A["sexid"]

In [43]:
lgb_dataset = lgb.Dataset(X_train, label=y_train, free_raw_data=False)

In [44]:
lgd_result = lgb.cv(parameters, lgb_dataset, n_rounds, folds=skf.split(X_train, y_train), early_stopping_rounds=10, verbose_eval=1, )

[1]	cv_agg's l1: 0.498848 + 1.87438e-05
[2]	cv_agg's l1: 0.497698 + 2.91916e-05
[3]	cv_agg's l1: 0.496555 + 3.72302e-05
[4]	cv_agg's l1: 0.495424 + 4.65656e-05
[5]	cv_agg's l1: 0.494118 + 8.34709e-05
[6]	cv_agg's l1: 0.493012 + 9.27971e-05
[7]	cv_agg's l1: 0.491925 + 0.000104746
[8]	cv_agg's l1: 0.490642 + 0.000143939
[9]	cv_agg's l1: 0.489567 + 0.000144134
[10]	cv_agg's l1: 0.489122 + 0.000159335
[11]	cv_agg's l1: 0.488068 + 0.000166771
[12]	cv_agg's l1: 0.487024 + 0.000174606
[13]	cv_agg's l1: 0.485966 + 0.00017624
[14]	cv_agg's l1: 0.484781 + 0.000190381
[15]	cv_agg's l1: 0.48376 + 0.000182319
[16]	cv_agg's l1: 0.483335 + 0.000186915
[17]	cv_agg's l1: 0.482314 + 0.000222037
[18]	cv_agg's l1: 0.481318 + 0.000248576
[19]	cv_agg's l1: 0.480315 + 0.000248776
[20]	cv_agg's l1: 0.479331 + 0.000253829
[21]	cv_agg's l1: 0.478375 + 0.000255525
[22]	cv_agg's l1: 0.477455 + 0.000263894
[23]	cv_agg's l1: 0.476341 + 0.000279952
[24]	cv_agg's l1: 0.475388 + 0.000262674
[25]	cv_agg's l1: 0.474433 

[203]	cv_agg's l1: 0.381785 + 0.000942391
[204]	cv_agg's l1: 0.381512 + 0.000942641
[205]	cv_agg's l1: 0.381229 + 0.000893375
[206]	cv_agg's l1: 0.380984 + 0.000887947
[207]	cv_agg's l1: 0.380811 + 0.000891715
[208]	cv_agg's l1: 0.380501 + 0.000897305
[209]	cv_agg's l1: 0.380196 + 0.000962313
[210]	cv_agg's l1: 0.379923 + 0.00100573
[211]	cv_agg's l1: 0.37959 + 0.000971431
[212]	cv_agg's l1: 0.379305 + 0.000929817
[213]	cv_agg's l1: 0.379139 + 0.000919867
[214]	cv_agg's l1: 0.378848 + 0.000915847
[215]	cv_agg's l1: 0.378525 + 0.000877429
[216]	cv_agg's l1: 0.378244 + 0.000865254
[217]	cv_agg's l1: 0.378022 + 0.000884152
[218]	cv_agg's l1: 0.377855 + 0.000870846
[219]	cv_agg's l1: 0.377686 + 0.000869527
[220]	cv_agg's l1: 0.377418 + 0.000837781
[221]	cv_agg's l1: 0.377161 + 0.000880386
[222]	cv_agg's l1: 0.376926 + 0.000883285
[223]	cv_agg's l1: 0.37677 + 0.000879658
[224]	cv_agg's l1: 0.376471 + 0.000902725
[225]	cv_agg's l1: 0.376266 + 0.00090043
[226]	cv_agg's l1: 0.376038 + 0.000799

[403]	cv_agg's l1: 0.34032 + 0.00146752
[404]	cv_agg's l1: 0.340138 + 0.00145793
[405]	cv_agg's l1: 0.339947 + 0.00141325
[406]	cv_agg's l1: 0.339775 + 0.001388
[407]	cv_agg's l1: 0.339609 + 0.00144739
[408]	cv_agg's l1: 0.339452 + 0.00147082
[409]	cv_agg's l1: 0.339287 + 0.00144731
[410]	cv_agg's l1: 0.339157 + 0.00144714
[411]	cv_agg's l1: 0.339016 + 0.0014339
[412]	cv_agg's l1: 0.338901 + 0.00143207
[413]	cv_agg's l1: 0.338729 + 0.0014514
[414]	cv_agg's l1: 0.338576 + 0.00149201
[415]	cv_agg's l1: 0.338398 + 0.00149304
[416]	cv_agg's l1: 0.338262 + 0.00148989
[417]	cv_agg's l1: 0.338124 + 0.00146094
[418]	cv_agg's l1: 0.337972 + 0.0014106
[419]	cv_agg's l1: 0.337844 + 0.00141035
[420]	cv_agg's l1: 0.337688 + 0.00141297
[421]	cv_agg's l1: 0.337548 + 0.00142524
[422]	cv_agg's l1: 0.337414 + 0.00144852
[423]	cv_agg's l1: 0.337217 + 0.00140006
[424]	cv_agg's l1: 0.337056 + 0.00138351
[425]	cv_agg's l1: 0.336864 + 0.00143813
[426]	cv_agg's l1: 0.336707 + 0.00142458
[427]	cv_agg's l1: 0.3

[607]	cv_agg's l1: 0.312378 + 0.00210804
[608]	cv_agg's l1: 0.312251 + 0.00209164
[609]	cv_agg's l1: 0.312116 + 0.00208684
[610]	cv_agg's l1: 0.311981 + 0.00208047
[611]	cv_agg's l1: 0.311925 + 0.00208088
[612]	cv_agg's l1: 0.311787 + 0.0020736
[613]	cv_agg's l1: 0.311666 + 0.002058
[614]	cv_agg's l1: 0.311528 + 0.00203575
[615]	cv_agg's l1: 0.311382 + 0.00202632
[616]	cv_agg's l1: 0.31123 + 0.00201153
[617]	cv_agg's l1: 0.311108 + 0.00201968
[618]	cv_agg's l1: 0.310998 + 0.00201504
[619]	cv_agg's l1: 0.310872 + 0.00201644
[620]	cv_agg's l1: 0.310794 + 0.00202358
[621]	cv_agg's l1: 0.310651 + 0.00203963
[622]	cv_agg's l1: 0.310495 + 0.00204921
[623]	cv_agg's l1: 0.310375 + 0.00201585
[624]	cv_agg's l1: 0.310257 + 0.00198681
[625]	cv_agg's l1: 0.310147 + 0.00197632
[626]	cv_agg's l1: 0.31004 + 0.00196048
[627]	cv_agg's l1: 0.309922 + 0.00194131
[628]	cv_agg's l1: 0.309809 + 0.00190671
[629]	cv_agg's l1: 0.309641 + 0.00193337
[630]	cv_agg's l1: 0.309483 + 0.00196631
[631]	cv_agg's l1: 0.

[808]	cv_agg's l1: 0.291142 + 0.00212594
[809]	cv_agg's l1: 0.291057 + 0.0021443
[810]	cv_agg's l1: 0.29095 + 0.00213411
[811]	cv_agg's l1: 0.290785 + 0.00208755
[812]	cv_agg's l1: 0.290624 + 0.00204305
[813]	cv_agg's l1: 0.290589 + 0.00204487
[814]	cv_agg's l1: 0.290473 + 0.00202204
[815]	cv_agg's l1: 0.290374 + 0.00201119
[816]	cv_agg's l1: 0.290248 + 0.00200872
[817]	cv_agg's l1: 0.290127 + 0.00196956
[818]	cv_agg's l1: 0.289983 + 0.00193763
[819]	cv_agg's l1: 0.289883 + 0.00192427
[820]	cv_agg's l1: 0.289791 + 0.00192856
[821]	cv_agg's l1: 0.289692 + 0.00194323
[822]	cv_agg's l1: 0.289602 + 0.00194485
[823]	cv_agg's l1: 0.28957 + 0.00194441
[824]	cv_agg's l1: 0.289464 + 0.00194617
[825]	cv_agg's l1: 0.289406 + 0.00195827
[826]	cv_agg's l1: 0.289332 + 0.00197728
[827]	cv_agg's l1: 0.289245 + 0.00200226
[828]	cv_agg's l1: 0.289164 + 0.00202368
[829]	cv_agg's l1: 0.289096 + 0.0020765
[830]	cv_agg's l1: 0.289016 + 0.00212607
[831]	cv_agg's l1: 0.288926 + 0.00208967
[832]	cv_agg's l1: 0

...

[19097]	cv_agg's l1: 0.0996952 + 0.00131841
[19098]	cv_agg's l1: 0.0996947 + 0.00131854
[19099]	cv_agg's l1: 0.0996921 + 0.00131938
[19100]	cv_agg's l1: 0.0996902 + 0.00132066
[19101]	cv_agg's l1: 0.099688 + 0.0013195
[19102]	cv_agg's l1: 0.0996851 + 0.00131911
[19103]	cv_agg's l1: 0.0996824 + 0.0013171
[19104]	cv_agg's l1: 0.0996793 + 0.00131533
[19105]	cv_agg's l1: 0.0996774 + 0.00131542
[19106]	cv_agg's l1: 0.0996758 + 0.00131541
[19107]	cv_agg's l1: 0.0996732 + 0.00131512
[19108]	cv_agg's l1: 0.0996729 + 0.00131489
[19109]	cv_agg's l1: 0.0996714 + 0.00131402
[19110]	cv_agg's l1: 0.0996711 + 0.00131415
[19111]	cv_agg's l1: 0.0996687 + 0.00131535
[19112]	cv_agg's l1: 0.0996656 + 0.00131541
[19113]	cv_agg's l1: 0.0996649 + 0.00131558
[19114]	cv_agg's l1: 0.0996635 + 0.00131498
[19115]	cv_agg's l1: 0.0996617 + 0.00131562
[19116]	cv_agg's l1: 0.0996602 + 0.00131609
[19117]	cv_agg's l1: 0.0996586 + 0.00131596
[19118]	cv_agg's l1: 0.0996573 + 0.00131568
[19119]	cv_agg's l1: 0.0996549 + 0.

[19291]	cv_agg's l1: 0.0992986 + 0.00131119
[19292]	cv_agg's l1: 0.0992976 + 0.00131123
[19293]	cv_agg's l1: 0.0992943 + 0.0013107
[19294]	cv_agg's l1: 0.0992911 + 0.00131029
[19295]	cv_agg's l1: 0.0992893 + 0.00131034
[19296]	cv_agg's l1: 0.0992875 + 0.001311
[19297]	cv_agg's l1: 0.0992868 + 0.00131123
[19298]	cv_agg's l1: 0.0992836 + 0.00131336
[19299]	cv_agg's l1: 0.0992833 + 0.00131345
[19300]	cv_agg's l1: 0.0992829 + 0.00131366
[19301]	cv_agg's l1: 0.0992818 + 0.00131351
[19302]	cv_agg's l1: 0.0992808 + 0.00131346
[19303]	cv_agg's l1: 0.0992796 + 0.00131464
[19304]	cv_agg's l1: 0.0992779 + 0.00131498
[19305]	cv_agg's l1: 0.099276 + 0.00131527
[19306]	cv_agg's l1: 0.0992741 + 0.00131566
[19307]	cv_agg's l1: 0.0992703 + 0.00131615
[19308]	cv_agg's l1: 0.0992677 + 0.00131726
[19309]	cv_agg's l1: 0.099267 + 0.001318
[19310]	cv_agg's l1: 0.0992654 + 0.00131729
[19311]	cv_agg's l1: 0.0992627 + 0.00131747
[19312]	cv_agg's l1: 0.0992606 + 0.00131781
[19313]	cv_agg's l1: 0.0992586 + 0.0013

[19479]	cv_agg's l1: 0.0989303 + 0.00132803
[19480]	cv_agg's l1: 0.0989274 + 0.00132682
[19481]	cv_agg's l1: 0.0989247 + 0.00132667
[19482]	cv_agg's l1: 0.0989219 + 0.00132665
[19483]	cv_agg's l1: 0.0989194 + 0.00132562
[19484]	cv_agg's l1: 0.0989165 + 0.00132429
[19485]	cv_agg's l1: 0.0989145 + 0.00132392
[19486]	cv_agg's l1: 0.0989141 + 0.00132383
[19487]	cv_agg's l1: 0.098912 + 0.0013234
[19488]	cv_agg's l1: 0.0989096 + 0.001323
[19489]	cv_agg's l1: 0.0989059 + 0.00132144
[19490]	cv_agg's l1: 0.0989027 + 0.00132031
[19491]	cv_agg's l1: 0.0989007 + 0.00131838
[19492]	cv_agg's l1: 0.0988987 + 0.00131645
[19493]	cv_agg's l1: 0.0988955 + 0.00131759
[19494]	cv_agg's l1: 0.0988927 + 0.00131828
[19495]	cv_agg's l1: 0.0988905 + 0.00131928
[19496]	cv_agg's l1: 0.0988897 + 0.00131995
[19497]	cv_agg's l1: 0.098889 + 0.00132042
[19498]	cv_agg's l1: 0.0988885 + 0.00132088
[19499]	cv_agg's l1: 0.098886 + 0.00132116
[19500]	cv_agg's l1: 0.0988837 + 0.00132147
[19501]	cv_agg's l1: 0.0988811 + 0.001

[19677]	cv_agg's l1: 0.0985257 + 0.00130012
[19678]	cv_agg's l1: 0.0985239 + 0.0013008
[19679]	cv_agg's l1: 0.0985223 + 0.00130131
[19680]	cv_agg's l1: 0.0985197 + 0.00130253
[19681]	cv_agg's l1: 0.0985185 + 0.00130111
[19682]	cv_agg's l1: 0.0985168 + 0.00129974
[19683]	cv_agg's l1: 0.0985162 + 0.00129958
[19684]	cv_agg's l1: 0.0985142 + 0.00130019
[19685]	cv_agg's l1: 0.0985116 + 0.00130208
[19686]	cv_agg's l1: 0.0985098 + 0.00130335
[19687]	cv_agg's l1: 0.0985085 + 0.00130361
[19688]	cv_agg's l1: 0.098508 + 0.0013031
[19689]	cv_agg's l1: 0.0985073 + 0.00130293
[19690]	cv_agg's l1: 0.098505 + 0.00130289
[19691]	cv_agg's l1: 0.098503 + 0.00130203
[19692]	cv_agg's l1: 0.0985008 + 0.00130109
[19693]	cv_agg's l1: 0.0984982 + 0.00130119
[19694]	cv_agg's l1: 0.0984969 + 0.00130033
[19695]	cv_agg's l1: 0.0984938 + 0.00129891
[19696]	cv_agg's l1: 0.0984917 + 0.00129865
[19697]	cv_agg's l1: 0.0984872 + 0.00129795
[19698]	cv_agg's l1: 0.0984855 + 0.00129788
[19699]	cv_agg's l1: 0.0984833 + 0.00

[19867]	cv_agg's l1: 0.0981784 + 0.00131235
[19868]	cv_agg's l1: 0.098176 + 0.00131186
[19869]	cv_agg's l1: 0.0981743 + 0.00131306
[19870]	cv_agg's l1: 0.0981724 + 0.00131447
[19871]	cv_agg's l1: 0.098171 + 0.00131331
[19872]	cv_agg's l1: 0.0981686 + 0.00131142
[19873]	cv_agg's l1: 0.0981683 + 0.00131137
[19874]	cv_agg's l1: 0.0981659 + 0.00131148
[19875]	cv_agg's l1: 0.0981646 + 0.00131235
[19876]	cv_agg's l1: 0.0981625 + 0.00131408
[19877]	cv_agg's l1: 0.098161 + 0.0013159
[19878]	cv_agg's l1: 0.0981581 + 0.0013167
[19879]	cv_agg's l1: 0.0981561 + 0.00131729
[19880]	cv_agg's l1: 0.0981539 + 0.00131774
[19881]	cv_agg's l1: 0.0981527 + 0.00131931
[19882]	cv_agg's l1: 0.0981509 + 0.00132089
[19883]	cv_agg's l1: 0.0981492 + 0.00132136
[19884]	cv_agg's l1: 0.0981481 + 0.00132179
[19885]	cv_agg's l1: 0.0981464 + 0.00132262
[19886]	cv_agg's l1: 0.0981448 + 0.00132343
[19887]	cv_agg's l1: 0.0981439 + 0.0013231
[19888]	cv_agg's l1: 0.0981431 + 0.00132318
[19889]	cv_agg's l1: 0.0981416 + 0.001

In [45]:
print(min(lgd_result['l1-mean']), len(lgd_result['l1-mean']))

0.09793006870297304 20000


In [46]:
bst_classifier = lgb.train(parameters, lgb_dataset, n_rounds)

In [47]:
test_df_A = test_df_A.sort_values(by='clientid')

In [48]:
predict = bst_classifier.predict(test_df_A,num_iteration=bst_classifier.best_iteration)

In [61]:
predict

array([0.78247128, 0.6061377 , 0.24966657, ..., 0.99044008, 0.97436967,
       0.99987989])

In [53]:
test_df_A["PREDICTION"] = predict

In [54]:
predict_mean = test_df_A.groupby("clientid")["PREDICTION"].mean()

# Submition

In [55]:
predict_mean = predict_mean.reset_index()

In [56]:
submition = pd.DataFrame({'clientid': predict_mean.clientid})
submition['sexid'] = predict_mean.PREDICTION
submition.to_csv('output_draft.csv', index=False)

In [57]:
submition.head()

clientid     sexid
0       521  0.542671
1       537  0.892326
2       541  0.961075
3       553  0.772171
4       570  0.904967

In [682]:
submition.head()

clientid     sexid
0       521  0.537067
1       537  0.880176
2       541  0.983337
3       553  0.777355
4       570  0.924851

In [58]:
result = pd.read_csv("output_draft.csv")

In [60]:
result.head()

clientid     sexid
0       521  0.542671
1       537  0.892326
2       541  0.961075
3       553  0.772171
4       570  0.904967

# Task B 

### Предлагаем вам поиграть в детектива. Все имеющиеся у нас данные вы найдёте в train_ds.csv.

### Мы знаем, что Джон Доу прилетел в Украину в начале июля 2015-го. Также известно, что 6го июля Джон ужинал в явочном кафе в Киеве и передал секретные документы другому шпиону, но в толпе наш агент его потерял.

### Отыщите место проживания Джона Доу.

In [63]:
from_timespan = (lambda x: datetime.datetime.fromtimestamp(x))

In [64]:
train_df["trandatetime"] = train_df["trandatetime"].apply(from_timespan)

In [65]:
train_df.head()

cgsettlementbufferid   mcc  tranccy  ccy  amount  \
0                     1  4131      978  980    6730   
1                     2  5651      978  980   55912   
2                     3  5812      978  980  135658   
3                     4  5947      978  980  138294   
4                     5  5651      978  980  426209   

                                   location        trandatetime  sexid  \
0  TRAMBESOS              SANT JOAN DES  ES 2013-12-02 11:49:22      1   
1  ZARA BARCELONA P GRACIABARCELONA      ES 2013-12-02 15:42:44      1   
2  CAFE DE L'ACADEMIA     BARCELONA      ES 2013-12-02 17:45:48      1   
3  2D BCN DISSENY EN BIJUTBARCELONA      ES 2013-12-02 17:59:39      1   
4  EL GANSO               BARCELONA      ES 2013-12-02 19:34:08      1   

   clientid  institution_transaction city_transaction country_transaction  
0        13                TRAMBESOS    SANT JOAN DES                  ES  
1        13  ZARA BARCELONA P GRACIA        BARCELONA                  ES  
2        13       CAFE DE L'ACADEMIA        BARCELONA                  ES  
3        13  2D BCN DISSENY EN BIJUT        BARCELONA                  ES  
4        13                 EL GANSO        BARCELONA                  ES

In [66]:
cities = ['KIEV','KYIV','KIYEV','KYIV UA','KIYEV UA','KIEV UA']

In [67]:
j_d = train_df[((train_df['trandatetime']>=pd.to_datetime("2015-06-06 18:00:00"))&
                (train_df['trandatetime']<pd.to_datetime("2015-06-07"))) 
               &
               ((train_df['city_transaction']==cities[0])|(train_df['city_transaction']==cities[1])|
                (train_df['city_transaction']==cities[2])|(train_df['city_transaction']==cities[3])|
                (train_df['city_transaction']==cities[4])|(train_df['city_transaction']==cities[5]))]

In [68]:
unique_id = j_d.clientid.unique()

In [70]:
unique_id

array([4731, 2166, 7705, 6535, 3523, 5744, 1133, 6584, 3753, 5749, 6197,
       5012, 5800, 4009, 1282, 2401, 8327, 9239, 6474, 4749, 3094, 3441,
       8824,  722, 5603, 8599, 2386,  724, 2391,  881, 2516, 8457, 6780],
      dtype=int64)

In [71]:
unique_id.size

33

In [73]:
train_df[(train_df["clientid"]==unique_id[2])&
         (train_df['trandatetime']<pd.to_datetime("2015-06-01"))&
         (train_df["country_transaction"] =="UA")].sort_values(by='trandatetime')

Empty DataFrame
Columns: [cgsettlementbufferid, mcc, tranccy, ccy, amount, location, trandatetime, sexid, clientid, institution_transaction, city_transaction, country_transaction]
Index: []

In [74]:
train_df[(train_df["clientid"]==unique_id[17])&
         (train_df['trandatetime']<pd.to_datetime("2015-06-01"))&
         (train_df["country_transaction"] =="UA")].sort_values(by='trandatetime')

Empty DataFrame
Columns: [cgsettlementbufferid, mcc, tranccy, ccy, amount, location, trandatetime, sexid, clientid, institution_transaction, city_transaction, country_transaction]
Index: []

In [75]:
train_df[train_df['clientid']==unique_id[2]].sort_values(by='trandatetime')

cgsettlementbufferid   mcc  tranccy  ccy  amount  \
74895                119622  6536      980  980   13800   
75764                121236  6012      980  980     500   
75765                121237  6012      980  980     100   
75783                121265  6538      980  980   13201   
75850                121211  5541      980  980   29992   
75851                121212  5541      980  980    7200   
75916                121316  5499      980  980   12000   
75911                121311  5541      980  980   72000   
75972                121397  5541      980  980    1800   
75973                121398  5541      980  980   24000   
76128                121751  5541      980  980   29992   
75431                120593  6536      980  980    2600   
75432                120594  6536      980  980     100   
75433                120595  6536      980  980   14300   
76204                121874  5541      980  980   30000   
78050                125408  6012      980  980  160000   
77922                125192  6536      980  980    3500   
77923                125193  6536      980  980   16500   
77924                125194  6536      980  980  100000   
78637                126268  5541      980  980   40000   
79259                127285  5541      980  980   39984   
79795                128001  5541      980  980   39984   
78969                126777  6536      980  980  120000   
79451                127415  6012      980  980  165000   
79352                127245  5541      980  980    9997   
...                     ...   ...      ...  ...     ...   
86250                137993  5541      980  980  120000   
86251                137994  5541      980  980   38076   
85747                137169  6536      980  980  166376   
86303                138093  5541      980  980   37900   
86307                138097  5541      980  980   48000   
86637                138564  5541      980  980   25200   
87368                139714  5541      980  980   30038   
86648                138578  6536      980  980  101200   
87370                139717  5541      980  980   60000   
87120                139234  5499      980  980    3150   
88311                141118  6536      980  980    8500   
88312                141119  6536      980  980   94588   
89030                142111  5541      980  980   24000   
89070                142360  5541      980  980   38326   
89740                143198  5541      980  980   38153   
90085                143877  5541      980  980    2190   
90214                144063  6536      980  980  210000   
90174                144055  6538      980  980  300000   
90604                144670  6536      980  980  150000   
90599                144664  6536      980  980   82700   
90926                145249  6012      980  980   80000   
90601                144666  6536      980  980   85000   
91550                146157  5541      980  980  180000   
91863                146411  5541      980  980   40000   
92511                147621  6536      980  980  200000   

                                       location        trandatetime  sexid  \
74895  MPPay2youAC            KYIV           UA 2015-06-04 17:04:45      1   
75764  MY.ALFABANK.UA         KIEV         UAUA 2015-06-05 04:19:01      1   
75765  MY.ALFABANK.UA         KIEV         UAUA 2015-06-05 04:29:20      1   
75783  TS000000               NOVOVOLYNSK  UAUA 2015-06-05 11:31:00      1   
75850  AZSVladimirskaya       LUTSK        UAUA 2015-06-05 12:41:37      1   
75851  AZSVladimirskaya       LUTSK        UAUA 2015-06-05 12:42:17      1   
75916  ProduktyVOY0           LUTSK        UAUA 2015-06-05 12:49:38      1   
75911  AZS WOG SOBORNOSTI     LUTSK        UAUA 2015-06-05 16:14:27      1   
75972  AZSVladimirskaya       LUTSK        UAUA 2015-06-05 17:18:54      1   
75973  AZS WOG 16 WOLYA       V OMELYANYK  UAUA 2015-06-05 17:22:21      1   
76128  AZS19VOLENERDZhI       NOVOVOLYNSK  UAUA 2015-06-06 17:11:10      1   
75

In [76]:
train_df[train_df['clientid']==unique_id[17]].sort_values(by='trandatetime')

cgsettlementbufferid   mcc  tranccy  ccy  amount  \
75902                121301  7399      980  980   36802   
76033                121561  5499      980  980    7670   
76050                121815  5812      980  980  168210   
76577                122618  5541      980  980  175212   
79427                127575  5812      980  980   36900   
81441                130454  5812      980  980   93400   
81483                130758  5812      980  980   25000   
86475                138318  5812      980  980   41802   
87679                140332  5921      980  980   80464   
89651                143103  5812      980  980   48800   
88994                142067  5411      980  980   29316   
89282                142495  5499      980  980   10536   
89598                143312  5655      980  980  163500   
89715                143315  5655      980  980   40000   
89730                143172  5812      980  980   73400   
90611                144596  5812      980  980    2700   
90612                144597  5812      980  980   29001   
91682                146214  5812      980  980   37304   
91839                146382  7011      980  980  240825   
91852                146399  5812      980  980   83950   

                                       location        trandatetime  sexid  \
75902  SYTO-PIANO             KYIV         UAUA 2015-06-04 15:32:00      1   
76033  EKOPOZ                 KIYEV        UAUA 2015-06-06 13:18:17      1   
76050  PANAROMARESTAURANT     KIYEV        UAUA 2015-06-06 21:47:37      1   
76577  SOCAR PETROL STATIONS  KYIV         UAUA 2015-06-07 12:47:42      1   
79427  DUKHMYANA PICH         LESINKI        UA 2015-06-15 15:54:23      1   
81441  ALMERIJA PLAZA GULLIVE KYIV         UAUA 2015-06-20 01:58:13      1   
81483  DaliPark               KIYEV        UAUA 2015-06-21 01:49:16      1   
86475  PESTO CAFE             KYIV         UAUA 2015-07-02 22:25:42      1   
87679  WINE TIME              KYIV         UAUA 2015-07-07 20:17:59      1   
89651  HASTRO KAFE TARELKA    KYIV         UAUA 2015-07-10 15:40:27      1   
88994  TMETRO10               KIYEV        UAUA 2015-07-10 16:09:17      1   
89282  GELATERIAROMA          KIYEV        UAUA 2015-07-11 20:33:37      1   
89598  ARENA                  KYIV         UAUA 2015-07-11 21:09:10      1   
89715  ARENA                  KYIV         UAUA 2015-07-11 21:24:08      1   
89730  OKHOTA NA OVETS        KYIV         UAUA 2015-07-12 20:02:36      1   
90611  KOZATSKIY STAN         KYIV         UAUA 2015-07-15 16:22:09      1   
90612  RESTAURANT GETMANSKYY  KYIV         UAUA 2015-07-15 16:22:47      1   
91682  CHPVECHER              ZHITOMIR     UAUA 2015-07-17 11:46:02      1   
91839  RADISSONBLU            YAREMCHE     UAUA 2015-07-17 22:07:24      1   
91852  COZACHOK               YAREMCHE     UAUA 2015-07-17 23:42:49      1   

       clientid institution_transaction city_transaction country_transaction  
75902      9239              SYTO-PIANO          KYIV UA                  UA  
76033      9239                  EKOPOZ         KIYEV UA                  UA  
76050      9239      PANAROMARESTAURANT         KIYEV UA                  UA  
76577      9239   SOCAR PETROL STATIONS          KYIV UA                  UA  
79427      9239          DUKHMYANA PICH          LESINKI                  UA  
81441      9239  ALMERIJA PLAZA GULLIVE          KYIV UA                  UA  
81483      9239                DaliPark         KIYEV UA                  UA  
86475      9239              PESTO CAFE          KYIV UA                  UA  
87679      9239               WINE TIME          KYIV UA                  UA  
89651      9239     HASTRO KAFE TARELKA          KYIV UA                  UA  
88994      9239                TMETRO10         KIYEV UA                  UA  
89282      9239           GELATERIAROMA         KIYEV UA                  UA  
89598      9239                   ARENA          KYIV UA                  UA  
89715      9239       

# John Dou id 9239 and he lives in Radisson Blu hotel in YAREMCHE UA

# Task A

In [536]:
train_df_A = train_df.copy()
test_df_A = test_df.copy()

In [537]:
#train_df_A.drop(["location","city_transaction","country_transaction"],axis=1,inplace=True)
#test_df_A.drop(["location","city_transaction","country_transaction"],axis=1,inplace=True)
train_df_A.drop(["location"],axis=1,inplace=True)
test_df_A.drop(["location"],axis=1,inplace=True)

In [538]:
train_df_A.info()

<class 'pandas.core.frame.DataFrame'>
RangeIndex: 92700 entries, 0 to 92699
Data columns (total 11 columns):
cgsettlementbufferid       92700 non-null int64
mcc                        92700 non-null int64
tranccy                    92700 non-null int64
ccy                        92700 non-null int64
amount                     92700 non-null int64
trandatetime               92700 non-null datetime64[ns]
sexid                      92700 non-null int64
clientid                   92700 non-null int64
institution_transaction    92700 non-null object
city_transaction           92700 non-null object
country_transaction        92700 non-null object
dtypes: datetime64[ns](1), int64(7), object(3)
memory usage: 7.8+ MB


In [539]:
test_df_A.info()

<class 'pandas.core.frame.DataFrame'>
RangeIndex: 40559 entries, 0 to 40558
Data columns (total 10 columns):
cgsettlementbufferid       40559 non-null int64
mcc                        40559 non-null int64
tranccy                    40559 non-null int64
ccy                        40559 non-null int64
amount                     40559 non-null int64
trandatetime               40559 non-null int64
clientid                   40559 non-null int64
institution_transaction    40559 non-null object
city_transaction           40559 non-null object
country_transaction        40559 non-null object
dtypes: int64(7), object(3)
memory usage: 3.1+ MB


In [540]:
to_timespan = (lambda x: time.mktime(x.timetuple()))

In [541]:
train_df_A["trandatetime"] = train_df_A["trandatetime"].apply(to_timespan).astype(np.int64)

In [542]:
train_df_A.head()

cgsettlementbufferid   mcc  tranccy  ccy  amount  trandatetime  sexid  \
0                     1  4131      978  980    6730    1385977762      1   
1                     2  5651      978  980   55912    1385991764      1   
2                     3  5812      978  980  135658    1385999148      1   
3                     4  5947      978  980  138294    1385999979      1   
4                     5  5651      978  980  426209    1386005648      1   

   clientid  institution_transaction city_transaction country_transaction  
0        13                TRAMBESOS    SANT JOAN DES                  ES  
1        13  ZARA BARCELONA P GRACIA        BARCELONA                  ES  
2        13       CAFE DE L'ACADEMIA        BARCELONA                  ES  
3        13  2D BCN DISSENY EN BIJUT        BARCELONA                  ES  
4        13                 EL GANSO        BARCELONA                  ES

In [543]:
categorical = [
    'institution_transaction',
    'city_transaction',
    'country_transaction'
]

In [544]:
#from collections import defaultdict
#from sklearn.preprocessing import LabelEncoder

def __encode_categorical(df_list, cat_cols):
    # initialize placeholder
    d = defaultdict(LabelEncoder)
    # fit and encode train/test,
    codes = pd.concat(
        [df[cat_cols] for df in df_list],
        axis=0
    ).fillna('').apply(
        lambda x: d[x.name].fit(x)
    ),
    # transform encodings to train/test etc
    for df in df_list:
        df[cat_cols] = df[cat_cols].fillna('').apply(
            lambda x: d[x.name].transform(x))

__encode_categorical(df_list=[train_df_A, test_df_A], cat_cols=categorical) 

In [545]:
train_df_A.head()

cgsettlementbufferid   mcc  tranccy  ccy  amount  trandatetime  sexid  \
0                     1  4131      978  980    6730    1385977762      1   
1                     2  5651      978  980   55912    1385991764      1   
2                     3  5812      978  980  135658    1385999148      1   
3                     4  5947      978  980  138294    1385999979      1   
4                     5  5651      978  980  426209    1386005648      1   

   clientid  institution_transaction  city_transaction  country_transaction  
0        13                    20316              2754                   30  
1        13                    22254               422                   30  
2        13                     5443               422                   30  
3        13                      653               422                   30  
4        13                     8015               422                   30

In [546]:
test_df_A.head()

cgsettlementbufferid   mcc  tranccy  ccy  amount  trandatetime  clientid  \
0                   395  5411      980  980    7488    1393172737       712   
1                   422  6010      980  980   40000    1393509649       766   
2                   429  6010      980  980  119000    1393583520       745   
3                   435  6010      980  980  210000    1393591808       748   
4                   445  6011      980  980   30000    1393766754       766   

   institution_transaction  city_transaction  country_transaction  
0                    21650              3198                   87  
1                    14491              2247                   87  
2                    14491              2247                   87  
3                    14491              2247                   87  
4                     9353              2247                   87

# Validation

In [547]:
X = train_df_A.drop(['sexid'], axis=1)
y = train_df_A['sexid']

In [550]:
skf = StratifiedKFold(n_splits=5, shuffle=True, random_state=42)

In [618]:
parameters={
   'objective': 'binary',
    'learning_rate': 0.01,
    'max_depth': 8,
    'num_threads': 4,
    'metric': 'mae',
    'seed': 42,
    'colsample_bytree': 0.9,
    'subsample': 0.9,
    'subsample_freq': 2,
    'min_data_in_leaf': 15,
}
n_rounds = 20000

In [554]:
(100/(train_df_A.shape[0]+test_df_A.shape[0]))*40559

30.43621819164184

In [593]:
X_train, X_val, y_train, y_val = train_test_split(X, y, test_size=0.304, random_state=42)

In [595]:
lgb_train = lgb.Dataset(X_train, label=y_train, free_raw_data=False)

In [619]:
lgd_classifier = lgb.cv(parameters, lgb_train, n_rounds, folds=skf.split(X_train, y_train), early_stopping_rounds=10, verbose_eval=1, )

[1]	cv_agg's l1: 0.498846 + 2.50491e-05
[2]	cv_agg's l1: 0.497694 + 3.86026e-05
[3]	cv_agg's l1: 0.496558 + 3.19498e-05
[4]	cv_agg's l1: 0.49543 + 4.67302e-05
[5]	cv_agg's l1: 0.494142 + 4.6937e-05
[6]	cv_agg's l1: 0.493031 + 5.73766e-05
[7]	cv_agg's l1: 0.491939 + 7.54259e-05
[8]	cv_agg's l1: 0.49074 + 7.55162e-05
[9]	cv_agg's l1: 0.489655 + 0.000105455
[10]	cv_agg's l1: 0.489219 + 0.000108827
[11]	cv_agg's l1: 0.488125 + 0.000151793
[12]	cv_agg's l1: 0.487045 + 0.000187498
[13]	cv_agg's l1: 0.486018 + 0.000193343
[14]	cv_agg's l1: 0.484868 + 0.000193753
[15]	cv_agg's l1: 0.483828 + 0.000199761
[16]	cv_agg's l1: 0.48339 + 0.000196544
[17]	cv_agg's l1: 0.482377 + 0.000223242
[18]	cv_agg's l1: 0.481352 + 0.000241812
[19]	cv_agg's l1: 0.48036 + 0.000282524
[20]	cv_agg's l1: 0.479405 + 0.000288329
[21]	cv_agg's l1: 0.478417 + 0.000291723
[22]	cv_agg's l1: 0.477448 + 0.000283489
[23]	cv_agg's l1: 0.47639 + 0.000265875
[24]	cv_agg's l1: 0.475425 + 0.000286881
[25]	cv_agg's l1: 0.474468 + 0.

[206]	cv_agg's l1: 0.381981 + 0.0014897
[207]	cv_agg's l1: 0.381815 + 0.00148956
[208]	cv_agg's l1: 0.381539 + 0.00144687
[209]	cv_agg's l1: 0.381292 + 0.00143569
[210]	cv_agg's l1: 0.381018 + 0.00140828
[211]	cv_agg's l1: 0.380803 + 0.0013689
[212]	cv_agg's l1: 0.380607 + 0.00132979
[213]	cv_agg's l1: 0.380451 + 0.00134042
[214]	cv_agg's l1: 0.38014 + 0.00138744
[215]	cv_agg's l1: 0.379847 + 0.00139822
[216]	cv_agg's l1: 0.379575 + 0.00140968
[217]	cv_agg's l1: 0.379314 + 0.00138243
[218]	cv_agg's l1: 0.379139 + 0.00138259
[219]	cv_agg's l1: 0.378987 + 0.00138838
[220]	cv_agg's l1: 0.378701 + 0.00134705
[221]	cv_agg's l1: 0.378421 + 0.00130147
[222]	cv_agg's l1: 0.378091 + 0.00126992
[223]	cv_agg's l1: 0.377927 + 0.00127068
[224]	cv_agg's l1: 0.377678 + 0.00127837
[225]	cv_agg's l1: 0.377408 + 0.00128094
[226]	cv_agg's l1: 0.377079 + 0.00124217
[227]	cv_agg's l1: 0.37681 + 0.00127909
[228]	cv_agg's l1: 0.376549 + 0.00131431
[229]	cv_agg's l1: 0.376398 + 0.00132196
[230]	cv_agg's l1: 0

[409]	cv_agg's l1: 0.341306 + 0.00192831
[410]	cv_agg's l1: 0.34114 + 0.00195582
[411]	cv_agg's l1: 0.340954 + 0.00196011
[412]	cv_agg's l1: 0.34078 + 0.00193007
[413]	cv_agg's l1: 0.340593 + 0.00193608
[414]	cv_agg's l1: 0.340426 + 0.00195385
[415]	cv_agg's l1: 0.34027 + 0.00197285
[416]	cv_agg's l1: 0.340109 + 0.00202123
[417]	cv_agg's l1: 0.339991 + 0.0019961
[418]	cv_agg's l1: 0.339882 + 0.00198654
[419]	cv_agg's l1: 0.339707 + 0.00201966
[420]	cv_agg's l1: 0.339549 + 0.00198727
[421]	cv_agg's l1: 0.339377 + 0.00201035
[422]	cv_agg's l1: 0.339199 + 0.0020311
[423]	cv_agg's l1: 0.339047 + 0.00208053
[424]	cv_agg's l1: 0.338893 + 0.00212711
[425]	cv_agg's l1: 0.338741 + 0.00207235
[426]	cv_agg's l1: 0.338572 + 0.0020703
[427]	cv_agg's l1: 0.338443 + 0.00206218
[428]	cv_agg's l1: 0.338323 + 0.00206572
[429]	cv_agg's l1: 0.338126 + 0.00202368
[430]	cv_agg's l1: 0.337943 + 0.00200721
[431]	cv_agg's l1: 0.337786 + 0.00198322
[432]	cv_agg's l1: 0.337645 + 0.00196767
[433]	cv_agg's l1: 0.3

[614]	cv_agg's l1: 0.313671 + 0.000874679
[615]	cv_agg's l1: 0.313551 + 0.00083796
[616]	cv_agg's l1: 0.31346 + 0.00086072
[617]	cv_agg's l1: 0.313344 + 0.000914505
[618]	cv_agg's l1: 0.313216 + 0.00096487
[619]	cv_agg's l1: 0.313112 + 0.00093833
[620]	cv_agg's l1: 0.312996 + 0.000924988
[621]	cv_agg's l1: 0.312904 + 0.00093078
[622]	cv_agg's l1: 0.312804 + 0.000937522
[623]	cv_agg's l1: 0.312729 + 0.000931338
[624]	cv_agg's l1: 0.312657 + 0.00092648
[625]	cv_agg's l1: 0.312587 + 0.000908765
[626]	cv_agg's l1: 0.312492 + 0.000920698
[627]	cv_agg's l1: 0.312407 + 0.000920028
[628]	cv_agg's l1: 0.312315 + 0.000932624
[629]	cv_agg's l1: 0.312164 + 0.00091982
[630]	cv_agg's l1: 0.312014 + 0.000912642
[631]	cv_agg's l1: 0.311882 + 0.000892839
[632]	cv_agg's l1: 0.311756 + 0.000867192
[633]	cv_agg's l1: 0.311644 + 0.000900542
[634]	cv_agg's l1: 0.311552 + 0.000901902
[635]	cv_agg's l1: 0.311424 + 0.000858436
[636]	cv_agg's l1: 0.311309 + 0.000808309
[637]	cv_agg's l1: 0.311191 + 0.000841472


[812]	cv_agg's l1: 0.293624 + 0.000814305
[813]	cv_agg's l1: 0.293592 + 0.000807922
[814]	cv_agg's l1: 0.293449 + 0.000824503
[815]	cv_agg's l1: 0.293355 + 0.000832014
[816]	cv_agg's l1: 0.29326 + 0.000842479
[817]	cv_agg's l1: 0.293155 + 0.000829137
[818]	cv_agg's l1: 0.293054 + 0.000818063
[819]	cv_agg's l1: 0.292923 + 0.000802527
[820]	cv_agg's l1: 0.292853 + 0.000791743
[821]	cv_agg's l1: 0.292742 + 0.000745383
[822]	cv_agg's l1: 0.292638 + 0.000698417
[823]	cv_agg's l1: 0.292601 + 0.00070082
[824]	cv_agg's l1: 0.292486 + 0.000719462
[825]	cv_agg's l1: 0.292413 + 0.000707742
[826]	cv_agg's l1: 0.292353 + 0.000687426
[827]	cv_agg's l1: 0.292281 + 0.000658996
[828]	cv_agg's l1: 0.292174 + 0.000608756
[829]	cv_agg's l1: 0.292071 + 0.000624469
[830]	cv_agg's l1: 0.291971 + 0.000642227
[831]	cv_agg's l1: 0.291856 + 0.000642431
[832]	cv_agg's l1: 0.291727 + 0.000664298
[833]	cv_agg's l1: 0.291642 + 0.000665973
[834]	cv_agg's l1: 0.291551 + 0.00067737
[835]	cv_agg's l1: 0.291432 + 0.00068

...

[19088]	cv_agg's l1: 0.106276 + 0.00214614
[19089]	cv_agg's l1: 0.106274 + 0.00214608
[19090]	cv_agg's l1: 0.106272 + 0.00214658
[19091]	cv_agg's l1: 0.106268 + 0.00215001
[19092]	cv_agg's l1: 0.106266 + 0.00215251
[19093]	cv_agg's l1: 0.106264 + 0.0021525
[19094]	cv_agg's l1: 0.106262 + 0.00215209
[19095]	cv_agg's l1: 0.106259 + 0.0021518
[19096]	cv_agg's l1: 0.106256 + 0.00215102
[19097]	cv_agg's l1: 0.106254 + 0.00214981
[19098]	cv_agg's l1: 0.106253 + 0.00214855
[19099]	cv_agg's l1: 0.10625 + 0.00214965
[19100]	cv_agg's l1: 0.106249 + 0.00215121
[19101]	cv_agg's l1: 0.106245 + 0.00215012
[19102]	cv_agg's l1: 0.106242 + 0.00214909
[19103]	cv_agg's l1: 0.106241 + 0.00215057
[19104]	cv_agg's l1: 0.10624 + 0.00215184
[19105]	cv_agg's l1: 0.106238 + 0.00215235
[19106]	cv_agg's l1: 0.106237 + 0.0021527
[19107]	cv_agg's l1: 0.106235 + 0.00215543
[19108]	cv_agg's l1: 0.106233 + 0.00215608
[19109]	cv_agg's l1: 0.106232 + 0.00215578
[19110]	cv_agg's l1: 0.106231 + 0.00215653
[19111]	cv_agg's

[19286]	cv_agg's l1: 0.1059 + 0.00215492
[19287]	cv_agg's l1: 0.105898 + 0.00215491
[19288]	cv_agg's l1: 0.105898 + 0.00215456
[19289]	cv_agg's l1: 0.105897 + 0.00215425
[19290]	cv_agg's l1: 0.105894 + 0.0021545
[19291]	cv_agg's l1: 0.105891 + 0.00215321
[19292]	cv_agg's l1: 0.105888 + 0.00215162
[19293]	cv_agg's l1: 0.105886 + 0.00215236
[19294]	cv_agg's l1: 0.105884 + 0.00215132
[19295]	cv_agg's l1: 0.105879 + 0.00215248
[19296]	cv_agg's l1: 0.105876 + 0.00215272
[19297]	cv_agg's l1: 0.105875 + 0.00215262
[19298]	cv_agg's l1: 0.105872 + 0.002154
[19299]	cv_agg's l1: 0.105871 + 0.00215303
[19300]	cv_agg's l1: 0.10587 + 0.00215212
[19301]	cv_agg's l1: 0.10587 + 0.00215207
[19302]	cv_agg's l1: 0.10587 + 0.0021513
[19303]	cv_agg's l1: 0.105868 + 0.00215162
[19304]	cv_agg's l1: 0.105867 + 0.00215167
[19305]	cv_agg's l1: 0.105865 + 0.00215257
[19306]	cv_agg's l1: 0.105864 + 0.00215419
[19307]	cv_agg's l1: 0.105861 + 0.00215405
[19308]	cv_agg's l1: 0.105858 + 0.00215433
[19309]	cv_agg's l1:

[19489]	cv_agg's l1: 0.105509 + 0.00213234
[19490]	cv_agg's l1: 0.105507 + 0.00213396
[19491]	cv_agg's l1: 0.105505 + 0.00213425
[19492]	cv_agg's l1: 0.105502 + 0.00213505
[19493]	cv_agg's l1: 0.105501 + 0.00213512
[19494]	cv_agg's l1: 0.105499 + 0.00213508
[19495]	cv_agg's l1: 0.105497 + 0.00213483
[19496]	cv_agg's l1: 0.105496 + 0.00213362
[19497]	cv_agg's l1: 0.105496 + 0.00213348
[19498]	cv_agg's l1: 0.105494 + 0.00213245
[19499]	cv_agg's l1: 0.105492 + 0.0021305
[19500]	cv_agg's l1: 0.105489 + 0.00212974
[19501]	cv_agg's l1: 0.105487 + 0.00212953
[19502]	cv_agg's l1: 0.105485 + 0.00212913
[19503]	cv_agg's l1: 0.105484 + 0.00212896
[19504]	cv_agg's l1: 0.105484 + 0.0021289
[19505]	cv_agg's l1: 0.105481 + 0.00212909
[19506]	cv_agg's l1: 0.105479 + 0.00212949
[19507]	cv_agg's l1: 0.105477 + 0.00212837
[19508]	cv_agg's l1: 0.105476 + 0.00212739
[19509]	cv_agg's l1: 0.105476 + 0.00212825
[19510]	cv_agg's l1: 0.105475 + 0.00212912
[19511]	cv_agg's l1: 0.105474 + 0.00212855
[19512]	cv_ag

[19690]	cv_agg's l1: 0.105145 + 0.00212728
[19691]	cv_agg's l1: 0.105144 + 0.00212719
[19692]	cv_agg's l1: 0.105141 + 0.00212477
[19693]	cv_agg's l1: 0.105137 + 0.00212531
[19694]	cv_agg's l1: 0.105133 + 0.00212605
[19695]	cv_agg's l1: 0.105132 + 0.0021257
[19696]	cv_agg's l1: 0.105131 + 0.00212637
[19697]	cv_agg's l1: 0.105129 + 0.00212639
[19698]	cv_agg's l1: 0.105128 + 0.00212596
[19699]	cv_agg's l1: 0.105127 + 0.00212647
[19700]	cv_agg's l1: 0.105125 + 0.00212762
[19701]	cv_agg's l1: 0.105123 + 0.00212901
[19702]	cv_agg's l1: 0.105121 + 0.00213014
[19703]	cv_agg's l1: 0.105119 + 0.00213075
[19704]	cv_agg's l1: 0.105117 + 0.00213147
[19705]	cv_agg's l1: 0.105116 + 0.00213211
[19706]	cv_agg's l1: 0.105115 + 0.00213256
[19707]	cv_agg's l1: 0.105114 + 0.00213132
[19708]	cv_agg's l1: 0.105113 + 0.0021311
[19709]	cv_agg's l1: 0.10511 + 0.00212783
[19710]	cv_agg's l1: 0.105107 + 0.00212454
[19711]	cv_agg's l1: 0.105106 + 0.00212493
[19712]	cv_agg's l1: 0.105103 + 0.00212781
[19713]	cv_agg

[19891]	cv_agg's l1: 0.104752 + 0.00214677
[19892]	cv_agg's l1: 0.104749 + 0.00214633
[19893]	cv_agg's l1: 0.104748 + 0.00214634
[19894]	cv_agg's l1: 0.104746 + 0.0021471
[19895]	cv_agg's l1: 0.104745 + 0.00214647
[19896]	cv_agg's l1: 0.104742 + 0.00214559
[19897]	cv_agg's l1: 0.10474 + 0.00214538
[19898]	cv_agg's l1: 0.104738 + 0.00214477
[19899]	cv_agg's l1: 0.104734 + 0.00214429
[19900]	cv_agg's l1: 0.104728 + 0.00214308
[19901]	cv_agg's l1: 0.104726 + 0.00214229
[19902]	cv_agg's l1: 0.104724 + 0.00214125
[19903]	cv_agg's l1: 0.10472 + 0.00214055
[19904]	cv_agg's l1: 0.104717 + 0.00213899
[19905]	cv_agg's l1: 0.104716 + 0.00213901
[19906]	cv_agg's l1: 0.104714 + 0.00213812
[19907]	cv_agg's l1: 0.10471 + 0.00214069
[19908]	cv_agg's l1: 0.10471 + 0.00214046
[19909]	cv_agg's l1: 0.104709 + 0.00214047
[19910]	cv_agg's l1: 0.104706 + 0.00214042
[19911]	cv_agg's l1: 0.104704 + 0.00213917
[19912]	cv_agg's l1: 0.104703 + 0.0021384
[19913]	cv_agg's l1: 0.104701 + 0.00213951
[19914]	cv_agg's 

In [620]:
print(min(lgd_classifier['l1-mean']), len(lgd_classifier['l1-mean']))

0.10453544178179294 20000


In [621]:
bst = lgb.train(parameters, lgb_train,n_rounds)

In [622]:
bst.best_iteration

0

In [623]:
predict_lgb = bst.predict(X_val,num_iteration=bst.best_iteration)

In [624]:
mean_absolute_error(y_val,predict_lgb)

0.09836847476008048

# Prediction

In [630]:
X_train = train_df_A.drop("sexid",axis=1)
y_train = train_df_A["sexid"]

In [631]:
lgb_dataset = lgb.Dataset(X_train, label=y_train, free_raw_data=False)

In [633]:
lgd_classifier = lgb.cv(parameters, lgb_dataset, n_rounds, folds=skf.split(X_train, y_train), early_stopping_rounds=10, verbose_eval=1, )

[1]	cv_agg's l1: 0.498848 + 1.87438e-05
[2]	cv_agg's l1: 0.497698 + 2.91916e-05
[3]	cv_agg's l1: 0.496555 + 3.72302e-05
[4]	cv_agg's l1: 0.495424 + 4.65656e-05
[5]	cv_agg's l1: 0.494118 + 8.34709e-05
[6]	cv_agg's l1: 0.493012 + 9.27971e-05
[7]	cv_agg's l1: 0.491925 + 0.000104746
[8]	cv_agg's l1: 0.490642 + 0.000143939
[9]	cv_agg's l1: 0.489567 + 0.000144134
[10]	cv_agg's l1: 0.489122 + 0.000159335
[11]	cv_agg's l1: 0.488068 + 0.000166771
[12]	cv_agg's l1: 0.487024 + 0.000174606
[13]	cv_agg's l1: 0.485966 + 0.00017624
[14]	cv_agg's l1: 0.484781 + 0.000190381
[15]	cv_agg's l1: 0.48376 + 0.000182319
[16]	cv_agg's l1: 0.483335 + 0.000186915
[17]	cv_agg's l1: 0.482314 + 0.000222037
[18]	cv_agg's l1: 0.481318 + 0.000248576
[19]	cv_agg's l1: 0.480315 + 0.000248776
[20]	cv_agg's l1: 0.479331 + 0.000253829
[21]	cv_agg's l1: 0.478375 + 0.000255525
[22]	cv_agg's l1: 0.477455 + 0.000263894
[23]	cv_agg's l1: 0.476341 + 0.000279952
[24]	cv_agg's l1: 0.475388 + 0.000262674
[25]	cv_agg's l1: 0.474433 

[207]	cv_agg's l1: 0.380811 + 0.000891715
[208]	cv_agg's l1: 0.380501 + 0.000897305
[209]	cv_agg's l1: 0.380196 + 0.000962313
[210]	cv_agg's l1: 0.379923 + 0.00100573
[211]	cv_agg's l1: 0.37959 + 0.000971431
[212]	cv_agg's l1: 0.379305 + 0.000929817
[213]	cv_agg's l1: 0.379139 + 0.000919867
[214]	cv_agg's l1: 0.378848 + 0.000915847
[215]	cv_agg's l1: 0.378525 + 0.000877429
[216]	cv_agg's l1: 0.378244 + 0.000865254
[217]	cv_agg's l1: 0.378022 + 0.000884152
[218]	cv_agg's l1: 0.377855 + 0.000870846
[219]	cv_agg's l1: 0.377686 + 0.000869527
[220]	cv_agg's l1: 0.377418 + 0.000837781
[221]	cv_agg's l1: 0.377161 + 0.000880386
[222]	cv_agg's l1: 0.376926 + 0.000883285
[223]	cv_agg's l1: 0.37677 + 0.000879658
[224]	cv_agg's l1: 0.376471 + 0.000902725
[225]	cv_agg's l1: 0.376266 + 0.00090043
[226]	cv_agg's l1: 0.376038 + 0.000799185
[227]	cv_agg's l1: 0.375782 + 0.000790374
[228]	cv_agg's l1: 0.375518 + 0.000802029
[229]	cv_agg's l1: 0.375354 + 0.000802248
[230]	cv_agg's l1: 0.375042 + 0.000828

[408]	cv_agg's l1: 0.339452 + 0.00147082
[409]	cv_agg's l1: 0.339287 + 0.00144731
[410]	cv_agg's l1: 0.339157 + 0.00144714
[411]	cv_agg's l1: 0.339016 + 0.0014339
[412]	cv_agg's l1: 0.338901 + 0.00143207
[413]	cv_agg's l1: 0.338729 + 0.0014514
[414]	cv_agg's l1: 0.338576 + 0.00149201
[415]	cv_agg's l1: 0.338398 + 0.00149304
[416]	cv_agg's l1: 0.338262 + 0.00148989
[417]	cv_agg's l1: 0.338124 + 0.00146094
[418]	cv_agg's l1: 0.337972 + 0.0014106
[419]	cv_agg's l1: 0.337844 + 0.00141035
[420]	cv_agg's l1: 0.337688 + 0.00141297
[421]	cv_agg's l1: 0.337548 + 0.00142524
[422]	cv_agg's l1: 0.337414 + 0.00144852
[423]	cv_agg's l1: 0.337217 + 0.00140006
[424]	cv_agg's l1: 0.337056 + 0.00138351
[425]	cv_agg's l1: 0.336864 + 0.00143813
[426]	cv_agg's l1: 0.336707 + 0.00142458
[427]	cv_agg's l1: 0.336551 + 0.00142869
[428]	cv_agg's l1: 0.336403 + 0.00143429
[429]	cv_agg's l1: 0.336273 + 0.00146109
[430]	cv_agg's l1: 0.336143 + 0.00148697
[431]	cv_agg's l1: 0.335998 + 0.00149643
[432]	cv_agg's l1: 

[612]	cv_agg's l1: 0.311787 + 0.0020736
[613]	cv_agg's l1: 0.311666 + 0.002058
[614]	cv_agg's l1: 0.311528 + 0.00203575
[615]	cv_agg's l1: 0.311382 + 0.00202632
[616]	cv_agg's l1: 0.31123 + 0.00201153
[617]	cv_agg's l1: 0.311108 + 0.00201968
[618]	cv_agg's l1: 0.310998 + 0.00201504
[619]	cv_agg's l1: 0.310872 + 0.00201644
[620]	cv_agg's l1: 0.310794 + 0.00202358
[621]	cv_agg's l1: 0.310651 + 0.00203963
[622]	cv_agg's l1: 0.310495 + 0.00204921
[623]	cv_agg's l1: 0.310375 + 0.00201585
[624]	cv_agg's l1: 0.310257 + 0.00198681
[625]	cv_agg's l1: 0.310147 + 0.00197632
[626]	cv_agg's l1: 0.31004 + 0.00196048
[627]	cv_agg's l1: 0.309922 + 0.00194131
[628]	cv_agg's l1: 0.309809 + 0.00190671
[629]	cv_agg's l1: 0.309641 + 0.00193337
[630]	cv_agg's l1: 0.309483 + 0.00196631
[631]	cv_agg's l1: 0.309382 + 0.00196062
[632]	cv_agg's l1: 0.309263 + 0.00197093
[633]	cv_agg's l1: 0.309193 + 0.00198356
[634]	cv_agg's l1: 0.309102 + 0.00200309
[635]	cv_agg's l1: 0.309 + 0.00199699
[636]	cv_agg's l1: 0.308

[819]	cv_agg's l1: 0.289883 + 0.00192427
[820]	cv_agg's l1: 0.289791 + 0.00192856
[821]	cv_agg's l1: 0.289692 + 0.00194323
[822]	cv_agg's l1: 0.289602 + 0.00194485
[823]	cv_agg's l1: 0.28957 + 0.00194441
[824]	cv_agg's l1: 0.289464 + 0.00194617
[825]	cv_agg's l1: 0.289406 + 0.00195827
[826]	cv_agg's l1: 0.289332 + 0.00197728
[827]	cv_agg's l1: 0.289245 + 0.00200226
[828]	cv_agg's l1: 0.289164 + 0.00202368
[829]	cv_agg's l1: 0.289096 + 0.0020765
[830]	cv_agg's l1: 0.289016 + 0.00212607
[831]	cv_agg's l1: 0.288926 + 0.00208967
[832]	cv_agg's l1: 0.288841 + 0.00205725
[833]	cv_agg's l1: 0.28873 + 0.00204337
[834]	cv_agg's l1: 0.288626 + 0.00203138
[835]	cv_agg's l1: 0.288494 + 0.00205427
[836]	cv_agg's l1: 0.28837 + 0.00207772
[837]	cv_agg's l1: 0.288315 + 0.00206742
[838]	cv_agg's l1: 0.288247 + 0.00207742
[839]	cv_agg's l1: 0.288174 + 0.00207195
[840]	cv_agg's l1: 0.288104 + 0.002067
[841]	cv_agg's l1: 0.288007 + 0.00205843
[842]	cv_agg's l1: 0.287914 + 0.00205179
[843]	cv_agg's l1: 0.2

...

[19118]	cv_agg's l1: 0.0996573 + 0.00131568
[19119]	cv_agg's l1: 0.0996549 + 0.00131503
[19120]	cv_agg's l1: 0.0996546 + 0.00131513
[19121]	cv_agg's l1: 0.0996522 + 0.00131426
[19122]	cv_agg's l1: 0.0996505 + 0.00131356
[19123]	cv_agg's l1: 0.0996498 + 0.00131376
[19124]	cv_agg's l1: 0.0996473 + 0.00131275
[19125]	cv_agg's l1: 0.0996446 + 0.00131292
[19126]	cv_agg's l1: 0.0996434 + 0.00131348
[19127]	cv_agg's l1: 0.0996414 + 0.00131356
[19128]	cv_agg's l1: 0.099641 + 0.00131377
[19129]	cv_agg's l1: 0.0996385 + 0.00131416
[19130]	cv_agg's l1: 0.0996384 + 0.00131437
[19131]	cv_agg's l1: 0.0996366 + 0.00131406
[19132]	cv_agg's l1: 0.099635 + 0.00131444
[19133]	cv_agg's l1: 0.0996338 + 0.00131362
[19134]	cv_agg's l1: 0.0996325 + 0.00131235
[19135]	cv_agg's l1: 0.0996305 + 0.0013131
[19136]	cv_agg's l1: 0.0996297 + 0.00131343
[19137]	cv_agg's l1: 0.0996265 + 0.00131014
[19138]	cv_agg's l1: 0.0996224 + 0.00130772
[19139]	cv_agg's l1: 0.0996216 + 0.00130763
[19140]	cv_agg's l1: 0.0996195 + 0.

[19312]	cv_agg's l1: 0.0992606 + 0.00131781
[19313]	cv_agg's l1: 0.0992586 + 0.00131746
[19314]	cv_agg's l1: 0.0992577 + 0.00131714
[19315]	cv_agg's l1: 0.0992553 + 0.00131692
[19316]	cv_agg's l1: 0.099253 + 0.00131619
[19317]	cv_agg's l1: 0.0992525 + 0.00131645
[19318]	cv_agg's l1: 0.099251 + 0.00131627
[19319]	cv_agg's l1: 0.0992505 + 0.00131626
[19320]	cv_agg's l1: 0.0992494 + 0.0013164
[19321]	cv_agg's l1: 0.0992473 + 0.00131655
[19322]	cv_agg's l1: 0.099242 + 0.0013172
[19323]	cv_agg's l1: 0.0992406 + 0.00131644
[19324]	cv_agg's l1: 0.0992391 + 0.001316
[19325]	cv_agg's l1: 0.0992347 + 0.0013192
[19326]	cv_agg's l1: 0.099231 + 0.00132055
[19327]	cv_agg's l1: 0.0992287 + 0.00131852
[19328]	cv_agg's l1: 0.0992285 + 0.00131807
[19329]	cv_agg's l1: 0.0992263 + 0.00131795
[19330]	cv_agg's l1: 0.0992244 + 0.00131808
[19331]	cv_agg's l1: 0.0992208 + 0.00132118
[19332]	cv_agg's l1: 0.0992181 + 0.00132202
[19333]	cv_agg's l1: 0.0992174 + 0.00132193
[19334]	cv_agg's l1: 0.099216 + 0.0013216

[19506]	cv_agg's l1: 0.0988686 + 0.00132
[19507]	cv_agg's l1: 0.0988655 + 0.00131852
[19508]	cv_agg's l1: 0.0988632 + 0.00131661
[19509]	cv_agg's l1: 0.0988632 + 0.00131684
[19510]	cv_agg's l1: 0.0988632 + 0.00131685
[19511]	cv_agg's l1: 0.0988603 + 0.00131697
[19512]	cv_agg's l1: 0.0988596 + 0.00131723
[19513]	cv_agg's l1: 0.0988589 + 0.00131698
[19514]	cv_agg's l1: 0.0988558 + 0.00131788
[19515]	cv_agg's l1: 0.0988544 + 0.00131817
[19516]	cv_agg's l1: 0.0988513 + 0.00131731
[19517]	cv_agg's l1: 0.098847 + 0.00132015
[19518]	cv_agg's l1: 0.0988433 + 0.0013208
[19519]	cv_agg's l1: 0.0988396 + 0.0013214
[19520]	cv_agg's l1: 0.0988361 + 0.00132261
[19521]	cv_agg's l1: 0.0988344 + 0.00132255
[19522]	cv_agg's l1: 0.0988317 + 0.00132168
[19523]	cv_agg's l1: 0.0988306 + 0.00132154
[19524]	cv_agg's l1: 0.0988299 + 0.00132114
[19525]	cv_agg's l1: 0.0988287 + 0.0013205
[19526]	cv_agg's l1: 0.0988274 + 0.00131986
[19527]	cv_agg's l1: 0.0988252 + 0.00131955
[19528]	cv_agg's l1: 0.0988228 + 0.0013

[19697]	cv_agg's l1: 0.0984872 + 0.00129795
[19698]	cv_agg's l1: 0.0984855 + 0.00129788
[19699]	cv_agg's l1: 0.0984833 + 0.0012971
[19700]	cv_agg's l1: 0.098481 + 0.00129645
[19701]	cv_agg's l1: 0.0984792 + 0.00129469
[19702]	cv_agg's l1: 0.0984764 + 0.00129228
[19703]	cv_agg's l1: 0.0984749 + 0.00129181
[19704]	cv_agg's l1: 0.0984731 + 0.00129185
[19705]	cv_agg's l1: 0.0984709 + 0.00129115
[19706]	cv_agg's l1: 0.0984698 + 0.00129077
[19707]	cv_agg's l1: 0.0984683 + 0.00129059
[19708]	cv_agg's l1: 0.0984671 + 0.00129014
[19709]	cv_agg's l1: 0.0984657 + 0.00129149
[19710]	cv_agg's l1: 0.0984649 + 0.0012924
[19711]	cv_agg's l1: 0.0984626 + 0.00129315
[19712]	cv_agg's l1: 0.0984614 + 0.00129322
[19713]	cv_agg's l1: 0.0984579 + 0.00129222
[19714]	cv_agg's l1: 0.0984573 + 0.00129187
[19715]	cv_agg's l1: 0.0984555 + 0.00129159
[19716]	cv_agg's l1: 0.0984555 + 0.00129235
[19717]	cv_agg's l1: 0.0984543 + 0.00129293
[19718]	cv_agg's l1: 0.0984532 + 0.00129344
[19719]	cv_agg's l1: 0.0984512 + 0.

[19892]	cv_agg's l1: 0.098137 + 0.00132248
[19893]	cv_agg's l1: 0.0981365 + 0.00132253
[19894]	cv_agg's l1: 0.0981346 + 0.00132354
[19895]	cv_agg's l1: 0.0981333 + 0.00132352
[19896]	cv_agg's l1: 0.098132 + 0.0013235
[19897]	cv_agg's l1: 0.0981295 + 0.00132233
[19898]	cv_agg's l1: 0.0981265 + 0.00132189
[19899]	cv_agg's l1: 0.0981245 + 0.00132303
[19900]	cv_agg's l1: 0.0981218 + 0.00132301
[19901]	cv_agg's l1: 0.0981188 + 0.00132353
[19902]	cv_agg's l1: 0.0981157 + 0.00132473
[19903]	cv_agg's l1: 0.0981134 + 0.00132446
[19904]	cv_agg's l1: 0.0981116 + 0.00132479
[19905]	cv_agg's l1: 0.0981101 + 0.0013248
[19906]	cv_agg's l1: 0.0981092 + 0.00132465
[19907]	cv_agg's l1: 0.0981054 + 0.00132081
[19908]	cv_agg's l1: 0.0981049 + 0.00132078
[19909]	cv_agg's l1: 0.0981041 + 0.00132099
[19910]	cv_agg's l1: 0.0981026 + 0.0013214
[19911]	cv_agg's l1: 0.0981014 + 0.0013216
[19912]	cv_agg's l1: 0.0981002 + 0.00132174
[19913]	cv_agg's l1: 0.0980986 + 0.00132154
[19914]	cv_agg's l1: 0.0980959 + 0.001

In [634]:
print(min(lgd_classifier['l1-mean']), len(lgd_classifier['l1-mean']))

0.09793006870297304 20000


In [635]:
bst = lgb.train(parameters, lgb_train,n_rounds)

In [639]:
test_df_A = test_df_A.sort_values(by='clientid')

In [640]:
predict = bst.predict(test_df_A,num_iteration=bst.best_iteration)

In [641]:
predict

array([0.78492853, 0.54422327, 0.21256299, ..., 0.98423111, 0.99584996,
       0.99969607])

In [644]:
test_df_A["PREDICTION"] = predict

In [647]:
predict_mean = test_df_A.groupby("clientid")["PREDICTION"].mean()

# Submition

In [675]:
predict_mean = predict_mean.reset_index()

In [680]:
submition = pd.DataFrame({'clientid': predict_mean.clientid})
submition['sexid'] = predict_mean.PREDICTION
submition.to_csv('output_draft.csv', index=False)

In [682]:
submition.head()

clientid     sexid
0       521  0.537067
1       537  0.880176
2       541  0.983337
3       553  0.777355
4       570  0.924851

In [683]:
result = pd.read_csv("output_draft.csv")

In [684]:
result

clientid     sexid
0         521  0.537067
1         537  0.880176
2         541  0.983337
3         553  0.777355
4         570  0.924851
5         591  0.910446
6         592  0.688923
7         599  0.413293
8         605  0.644449
9         629  0.777115
10        667  0.773328
11        694  0.424378
12        697  0.262033
13        700  0.901617
14        701  0.092313
15        706  0.360399
16        710  0.273763
17        711  0.212624
18        712  0.491165
19        713  0.227923
20        715  0.121967
21        716  0.171924
22        720  0.006359
23        723  0.993620
24        729  0.384402
..        ...       ...
971      9625  0.329859
972      9643  0.791263
973      9648  0.349638
974      9650  0.713157
975      9776  0.949330
976      9779  0.269041
977      9790  0.664839
978      9824  0.686161
979      9972  0.630404
980      9991  0.862087
981     10313  0.222934
982     10317  0.528044
983     10332  0.865063
984     10339  0.841342
985     10353  0.971074
986     10363  0.925045
987     10387  0.905299
988     10388  0.662034
989     10395  0.312137
990     10405  0.909841
991     10409  0.916476
992     10799  0.989613
993     11281  0.991162
994     11332  0.977280
995     11602  0.997773

[996 rows x 2 columns]

In [565]:
from sklearn.linear_model import LogisticRegression

In [582]:
classifier = LogisticRegression()

In [585]:
params = {
    'C': [0.01,0.1,0.9]
    }
log_reg_classifier = LogisticRegression(solver='newton-cg', class_weight='balanced', random_state=42,max_iter = 1000,n_jobs=n_jobs)

lgs_split = GridSearchCV(log_reg_classifier, params, scoring='neg_mean_absolute_error', cv=skf,verbose=2)
lgs_split.fit(X_train, y_train)
print ('gs.best_score_:', lgs_split.best_score_)

Fitting 5 folds for each of 3 candidates, totalling 15 fits
[CV] C=0.01 ..........................................................
[CV] ........................................... C=0.01, total=  11.1s
[CV] C=0.01 ..........................................................


[Parallel(n_jobs=1)]: Done   1 out of   1 | elapsed:   11.1s remaining:    0.0s


[CV] ........................................... C=0.01, total=   5.5s
[CV] C=0.01 ..........................................................
[CV] ........................................... C=0.01, total=  19.1s
[CV] C=0.01 ..........................................................
[CV] ........................................... C=0.01, total=  14.5s
[CV] C=0.01 ..........................................................
[CV] ........................................... C=0.01, total=   8.8s
[CV] C=0.1 ...........................................................
[CV] ............................................ C=0.1, total=  18.4s
[CV] C=0.1 ...........................................................
[CV] ............................................ C=0.1, total=   8.1s
[CV] C=0.1 ...........................................................
[CV] ............................................ C=0.1, total=  16.3s
[CV] C=0.1 ...........................................................
[CV] .

[Parallel(n_jobs=1)]: Done  15 out of  15 | elapsed:  3.3min finished


gs.best_score_: -0.45092143399618717


In [586]:
lgs_split.best_estimator_

LogisticRegression(C=0.1, class_weight='balanced', dual=False,
          fit_intercept=True, intercept_scaling=1, max_iter=1000,
          multi_class='ovr', n_jobs=3, penalty='l2', random_state=42,
          solver='newton-cg', tol=0.0001, verbose=0, warm_start=False)

In [587]:
lgs_best = lgs_split.best_estimator_

In [588]:
cv_score = np.mean(cross_val_score(lgs_best, X_train, y_train, scoring='neg_mean_absolute_error',n_jobs=n_jobs,verbose=1))

print("LogReg with train split:", cv_score) #0.7193249282374398 0.7231766475833975

LogReg with train split: -0.4515879023233258


[Parallel(n_jobs=3)]: Done   3 out of   3 | elapsed:   16.4s finished


In [590]:
y_crossval_predy_crossv  = lgs_best.predict_proba(X_val)

In [591]:
mean_absolute_error(y_val,y_crossval_predy_crossv[:,1])

0.4930464654958528

In [575]:
classifier.fit(X_train, y_train)

LogisticRegression(C=1.0, class_weight=None, dual=False, fit_intercept=True,
          intercept_scaling=1, max_iter=100, multi_class='ovr', n_jobs=1,
          penalty='l2', random_state=None, solver='liblinear', tol=0.0001,
          verbose=0, warm_start=False)

In [576]:
n_jobs

3

In [577]:
cv_score = np.mean(cross_val_score(classifier, X_train, y_train, scoring='mean_absolute_error',n_jobs=n_jobs,verbose=1))

[Parallel(n_jobs=3)]: Done   3 out of   3 | elapsed:    7.6s finished


In [578]:
print("LogReg with train split:", cv_score)

LogReg with train split: -0.43125280911786396


In [579]:
y_crossval_predy_crossv  = classifier.predict_proba(X_val)

In [581]:
mean_absolute_error(y_val,y_crossval_predy_crossv[:,1])

0.48863212620957885

# #################################################################

In [285]:
train_df[train_df['clientid']==unique_ids[17]].sort_values(by='trandatetime')

cgsettlementbufferid   mcc  tranccy  ccy  amount  \
75902                121301  7399      980  980   36802   
76033                121561  5499      980  980    7670   
76050                121815  5812      980  980  168210   
76577                122618  5541      980  980  175212   
79427                127575  5812      980  980   36900   
81441                130454  5812      980  980   93400   
81483                130758  5812      980  980   25000   
86475                138318  5812      980  980   41802   
87679                140332  5921      980  980   80464   
89651                143103  5812      980  980   48800   
88994                142067  5411      980  980   29316   
89282                142495  5499      980  980   10536   
89598                143312  5655      980  980  163500   
89715                143315  5655      980  980   40000   
89730                143172  5812      980  980   73400   
90611                144596  5812      980  980    2700   
90612                144597  5812      980  980   29001   
91682                146214  5812      980  980   37304   
91839                146382  7011      980  980  240825   
91852                146399  5812      980  980   83950   

                                       location        trandatetime  sexid  \
75902  SYTO-PIANO             KYIV         UAUA 2015-06-04 15:32:00      1   
76033  EKOPOZ                 KIYEV        UAUA 2015-06-06 13:18:17      1   
76050  PANAROMARESTAURANT     KIYEV        UAUA 2015-06-06 21:47:37      1   
76577  SOCAR PETROL STATIONS  KYIV         UAUA 2015-06-07 12:47:42      1   
79427  DUKHMYANA PICH         LESINKI        UA 2015-06-15 15:54:23      1   
81441  ALMERIJA PLAZA GULLIVE KYIV         UAUA 2015-06-20 01:58:13      1   
81483  DaliPark               KIYEV        UAUA 2015-06-21 01:49:16      1   
86475  PESTO CAFE             KYIV         UAUA 2015-07-02 22:25:42      1   
87679  WINE TIME              KYIV         UAUA 2015-07-07 20:17:59      1   
89651  HASTRO KAFE TARELKA    KYIV         UAUA 2015-07-10 15:40:27      1   
88994  TMETRO10               KIYEV        UAUA 2015-07-10 16:09:17      1   
89282  GELATERIAROMA          KIYEV        UAUA 2015-07-11 20:33:37      1   
89598  ARENA                  KYIV         UAUA 2015-07-11 21:09:10      1   
89715  ARENA                  KYIV         UAUA 2015-07-11 21:24:08      1   
89730  OKHOTA NA OVETS        KYIV         UAUA 2015-07-12 20:02:36      1   
90611  KOZATSKIY STAN         KYIV         UAUA 2015-07-15 16:22:09      1   
90612  RESTAURANT GETMANSKYY  KYIV         UAUA 2015-07-15 16:22:47      1   
91682  CHPVECHER              ZHITOMIR     UAUA 2015-07-17 11:46:02      1   
91839  RADISSONBLU            YAREMCHE     UAUA 2015-07-17 22:07:24      1   
91852  COZACHOK               YAREMCHE     UAUA 2015-07-17 23:42:49      1   

       clientid institution_transaction city_transaction country_transaction  
75902      9239              SYTO-PIANO          KYIV UA                  UA  
76033      9239                  EKOPOZ         KIYEV UA                  UA  
76050      9239      PANAROMARESTAURANT         KIYEV UA                  UA  
76577      9239   SOCAR PETROL STATIONS          KYIV UA                  UA  
79427      9239          DUKHMYANA PICH          LESINKI                  UA  
81441      9239  ALMERIJA PLAZA GULLIVE          KYIV UA                  UA  
81483      9239                DaliPark         KIYEV UA                  UA  
86475      9239              PESTO CAFE          KYIV UA                  UA  
87679      9239               WINE TIME          KYIV UA                  UA  
89651      9239     HASTRO KAFE TARELKA          KYIV UA                  UA  
88994      9239                TMETRO10         KIYEV UA                  UA  
89282      9239           GELATERIAROMA         KIYEV UA                  UA  
89598      9239                   ARENA          KYIV UA                  UA  
89715      9239       

In [286]:
train_df[train_df['clientid']==unique_ids[2]].sort_values(by='trandatetime')

cgsettlementbufferid   mcc  tranccy  ccy  amount  \
74895                119622  6536      980  980   13800   
75764                121236  6012      980  980     500   
75765                121237  6012      980  980     100   
75783                121265  6538      980  980   13201   
75850                121211  5541      980  980   29992   
75851                121212  5541      980  980    7200   
75916                121316  5499      980  980   12000   
75911                121311  5541      980  980   72000   
75972                121397  5541      980  980    1800   
75973                121398  5541      980  980   24000   
76128                121751  5541      980  980   29992   
75431                120593  6536      980  980    2600   
75432                120594  6536      980  980     100   
75433                120595  6536      980  980   14300   
76204                121874  5541      980  980   30000   
78050                125408  6012      980  980  160000   
77922                125192  6536      980  980    3500   
77923                125193  6536      980  980   16500   
77924                125194  6536      980  980  100000   
78637                126268  5541      980  980   40000   
79259                127285  5541      980  980   39984   
79795                128001  5541      980  980   39984   
78969                126777  6536      980  980  120000   
79451                127415  6012      980  980  165000   
79352                127245  5541      980  980    9997   
...                     ...   ...      ...  ...     ...   
86250                137993  5541      980  980  120000   
86251                137994  5541      980  980   38076   
85747                137169  6536      980  980  166376   
86303                138093  5541      980  980   37900   
86307                138097  5541      980  980   48000   
86637                138564  5541      980  980   25200   
87368                139714  5541      980  980   30038   
86648                138578  6536      980  980  101200   
87370                139717  5541      980  980   60000   
87120                139234  5499      980  980    3150   
88311                141118  6536      980  980    8500   
88312                141119  6536      980  980   94588   
89030                142111  5541      980  980   24000   
89070                142360  5541      980  980   38326   
89740                143198  5541      980  980   38153   
90085                143877  5541      980  980    2190   
90214                144063  6536      980  980  210000   
90174                144055  6538      980  980  300000   
90604                144670  6536      980  980  150000   
90599                144664  6536      980  980   82700   
90926                145249  6012      980  980   80000   
90601                144666  6536      980  980   85000   
91550                146157  5541      980  980  180000   
91863                146411  5541      980  980   40000   
92511                147621  6536      980  980  200000   

                                       location        trandatetime  sexid  \
74895  MPPay2youAC            KYIV           UA 2015-06-04 17:04:45      1   
75764  MY.ALFABANK.UA         KIEV         UAUA 2015-06-05 04:19:01      1   
75765  MY.ALFABANK.UA         KIEV         UAUA 2015-06-05 04:29:20      1   
75783  TS000000               NOVOVOLYNSK  UAUA 2015-06-05 11:31:00      1   
75850  AZSVladimirskaya       LUTSK        UAUA 2015-06-05 12:41:37      1   
75851  AZSVladimirskaya       LUTSK        UAUA 2015-06-05 12:42:17      1   
75916  ProduktyVOY0           LUTSK        UAUA 2015-06-05 12:49:38      1   
75911  AZS WOG SOBORNOSTI     LUTSK        UAUA 2015-06-05 16:14:27      1   
75972  AZSVladimirskaya       LUTSK        UAUA 2015-06-05 17:18:54      1   
75973  AZS WOG 16 WOLYA       V OMELYANYK  UAUA 2015-06-05 17:22:21      1   
76128  AZS19VOLENERDZhI       NOVOVOLYNSK  UAUA 2015-06-06 17:11:10      1   
75

In [231]:
for i in range(0, unique_ids.size):
    train_df[(train_df["clientid"]==unique_ids[i])&(train_df['trandatetime']<pd.to_datetime("2015-06-01"))&((train_df['city_transaction']!=cities[0])&(train_df['city_transaction']!=cities[1])&(train_df['city_transaction']!=cities[2])&(train_df['city_transaction']!=cities[3])&(train_df['city_transaction']!=cities[4])&(train_df['city_transaction']!=cities[5]))]
        

In [68]:
list_of_locations = list()
for i in q:
    result = re.findall("Kiev",i)
    #print(result)
    if(result != []):
        list_of_locations.append(i)
    

In [70]:
list_of_locations[0]

'VBUA/12, LUGOVAYA      Kiev           UA'

In [36]:
result = re.findall("UA",q)

# A

In [16]:
categorical = [
    'location'
]

In [17]:
from collections import defaultdict
from sklearn.preprocessing import LabelEncoder

def __encode_categorical(df_list, cat_cols):
    # initialize placeholder
    d = defaultdict(LabelEncoder)
    # fit and encode train/test,
    codes = pd.concat(
        [df[cat_cols] for df in df_list],
        axis=0
    ).fillna('').apply(
        lambda x: d[x.name].fit(x)
    ),
    # transform encodings to train/test etc
    for df in df_list:
        df[cat_cols] = df[cat_cols].fillna('').apply(
            lambda x: d[x.name].transform(x))

__encode_categorical(df_list=[train, test], cat_cols=categorical) 

In [18]:
train.head()

cgsettlementbufferid   mcc  tranccy  ccy  amount  location  trandatetime  \
0                     1  4131      978  980    6730     23396    1385977762   
1                     2  5651      978  980   55912     25686    1385991764   
2                     3  5812      978  980  135658      6251    1385999148   
3                     4  5947      978  980  138294       684    1385999979   
4                     5  5651      978  980  426209      9209    1386005648   

   sexid  clientid  
0      1        13  
1      1        13  
2      1        13  
3      1        13  
4      1        13

In [19]:
test.head()

cgsettlementbufferid   mcc  tranccy  ccy  amount  location  trandatetime  \
0                   395  5411      980  980    7488     24989    1393172737   
1                   422  6010      980  980   40000     16603    1393509649   
2                   429  6010      980  980  119000     16603    1393583520   
3                   435  6010      980  980  210000     16603    1393591808   
4                   445  6011      980  980   30000     10715    1393766754   

   clientid  
0       712  
1       766  
2       745  
3       748  
4       766

In [20]:
X.info()

<class 'pandas.core.frame.DataFrame'>
RangeIndex: 92700 entries, 0 to 92699
Data columns (total 8 columns):
cgsettlementbufferid    92700 non-null int64
mcc                     92700 non-null int64
tranccy                 92700 non-null int64
ccy                     92700 non-null int64
amount                  92700 non-null int64
location                92700 non-null object
trandatetime            92700 non-null int64
clientid                92700 non-null int64
dtypes: int64(7), object(1)
memory usage: 5.7+ MB


In [21]:
X = train.drop(['sexid'], axis=1)
y = train['sexid']

In [22]:
skf = StratifiedKFold(n_splits=5, shuffle=True, random_state=42)

In [45]:
parameters={
   'objective': 'binary',
    'learning_rate': 0.01,
    'max_depth': 8,
    'num_threads': 4,
    'metric': 'mae',
    'seed': 42,
    'colsample_bytree': 0.65,
    'subsample': 0.8,
    'subsample_freq': 2,
    'min_data_in_leaf': 15,
}
n_rounds = 10000

In [24]:
X.info()

<class 'pandas.core.frame.DataFrame'>
RangeIndex: 92700 entries, 0 to 92699
Data columns (total 8 columns):
cgsettlementbufferid    92700 non-null int64
mcc                     92700 non-null int64
tranccy                 92700 non-null int64
ccy                     92700 non-null int64
amount                  92700 non-null int64
location                92700 non-null int64
trandatetime            92700 non-null int64
clientid                92700 non-null int64
dtypes: int64(8)
memory usage: 5.7 MB


In [46]:
lgb_train = lgb.Dataset(X, label=y, free_raw_data=False)

In [52]:
result_base = lgb.cv(parameters, lgb_train, n_rounds, folds=skf.split(X, y), early_stopping_rounds=10, verbose_eval=1, )

[1]	cv_agg's l1: 0.499532 + 1.20864e-05
[2]	cv_agg's l1: 0.498193 + 3.41144e-05
[3]	cv_agg's l1: 0.49685 + 7.24828e-05
[4]	cv_agg's l1: 0.495522 + 0.000127925
[5]	cv_agg's l1: 0.495066 + 0.000125393
[6]	cv_agg's l1: 0.494664 + 0.000124388
[7]	cv_agg's l1: 0.493371 + 0.000170358
[8]	cv_agg's l1: 0.492098 + 0.000224003
[9]	cv_agg's l1: 0.491665 + 0.000224927
[10]	cv_agg's l1: 0.490342 + 0.000229421
[11]	cv_agg's l1: 0.489061 + 0.000235363
[12]	cv_agg's l1: 0.48777 + 0.000248661
[13]	cv_agg's l1: 0.486487 + 0.000266006
[14]	cv_agg's l1: 0.486067 + 0.000263326
[15]	cv_agg's l1: 0.484806 + 0.000280291
[16]	cv_agg's l1: 0.483566 + 0.000300069
[17]	cv_agg's l1: 0.483186 + 0.000297937
[18]	cv_agg's l1: 0.481964 + 0.000324032
[19]	cv_agg's l1: 0.480767 + 0.000360791
[20]	cv_agg's l1: 0.480417 + 0.000359396
[21]	cv_agg's l1: 0.479197 + 0.000379629
[22]	cv_agg's l1: 0.478797 + 0.000377022
[23]	cv_agg's l1: 0.478381 + 0.000368454
[24]	cv_agg's l1: 0.478167 + 0.00036813
[25]	cv_agg's l1: 0.476986 +

[203]	cv_agg's l1: 0.382707 + 0.000953124
[204]	cv_agg's l1: 0.382574 + 0.000960864
[205]	cv_agg's l1: 0.38243 + 0.000959834
[206]	cv_agg's l1: 0.382047 + 0.000906038
[207]	cv_agg's l1: 0.381943 + 0.000908575
[208]	cv_agg's l1: 0.381815 + 0.000897086
[209]	cv_agg's l1: 0.381443 + 0.000891541
[210]	cv_agg's l1: 0.381076 + 0.000867358
[211]	cv_agg's l1: 0.380939 + 0.000863706
[212]	cv_agg's l1: 0.380815 + 0.000877399
[213]	cv_agg's l1: 0.38046 + 0.000946595
[214]	cv_agg's l1: 0.380113 + 0.00100296
[215]	cv_agg's l1: 0.380008 + 0.0010014
[216]	cv_agg's l1: 0.379891 + 0.000995263
[217]	cv_agg's l1: 0.379785 + 0.000996163
[218]	cv_agg's l1: 0.379646 + 0.000997688
[219]	cv_agg's l1: 0.379312 + 0.000993161
[220]	cv_agg's l1: 0.3792 + 0.00098515
[221]	cv_agg's l1: 0.379099 + 0.000983653
[222]	cv_agg's l1: 0.378998 + 0.000982143
[223]	cv_agg's l1: 0.378926 + 0.000983115
[224]	cv_agg's l1: 0.378571 + 0.000972208
[225]	cv_agg's l1: 0.37825 + 0.000990262
[226]	cv_agg's l1: 0.377955 + 0.000990029
[

[403]	cv_agg's l1: 0.34857 + 0.000791454
[404]	cv_agg's l1: 0.348526 + 0.000792145
[405]	cv_agg's l1: 0.348328 + 0.000808847
[406]	cv_agg's l1: 0.348126 + 0.000834122
[407]	cv_agg's l1: 0.347984 + 0.000798485
[408]	cv_agg's l1: 0.347936 + 0.000795212
[409]	cv_agg's l1: 0.347772 + 0.00077603
[410]	cv_agg's l1: 0.347723 + 0.000774482
[411]	cv_agg's l1: 0.347568 + 0.000772592
[412]	cv_agg's l1: 0.347416 + 0.000771394
[413]	cv_agg's l1: 0.347246 + 0.000727909
[414]	cv_agg's l1: 0.347031 + 0.000713272
[415]	cv_agg's l1: 0.34692 + 0.000686464
[416]	cv_agg's l1: 0.346811 + 0.000662854
[417]	cv_agg's l1: 0.346772 + 0.000662078
[418]	cv_agg's l1: 0.346623 + 0.000650029
[419]	cv_agg's l1: 0.346561 + 0.000654164
[420]	cv_agg's l1: 0.346493 + 0.000654928
[421]	cv_agg's l1: 0.34633 + 0.000615559
[422]	cv_agg's l1: 0.346187 + 0.000588354
[423]	cv_agg's l1: 0.346133 + 0.000578876
[424]	cv_agg's l1: 0.346064 + 0.000575747
[425]	cv_agg's l1: 0.346005 + 0.000570092
[426]	cv_agg's l1: 0.345963 + 0.000568

[600]	cv_agg's l1: 0.323713 + 0.000868042
[601]	cv_agg's l1: 0.323492 + 0.000921281
[602]	cv_agg's l1: 0.32346 + 0.000919187
[603]	cv_agg's l1: 0.32336 + 0.000923227
[604]	cv_agg's l1: 0.323253 + 0.000930237
[605]	cv_agg's l1: 0.323162 + 0.00091523
[606]	cv_agg's l1: 0.323078 + 0.000899293
[607]	cv_agg's l1: 0.322921 + 0.000893873
[608]	cv_agg's l1: 0.322767 + 0.000885535
[609]	cv_agg's l1: 0.322736 + 0.000888356
[610]	cv_agg's l1: 0.32259 + 0.000884983
[611]	cv_agg's l1: 0.322412 + 0.000848207
[612]	cv_agg's l1: 0.32238 + 0.000850865
[613]	cv_agg's l1: 0.322255 + 0.000877971
[614]	cv_agg's l1: 0.322129 + 0.000904242
[615]	cv_agg's l1: 0.322091 + 0.0009058
[616]	cv_agg's l1: 0.32197 + 0.000879182
[617]	cv_agg's l1: 0.321808 + 0.000864649
[618]	cv_agg's l1: 0.321651 + 0.000845785
[619]	cv_agg's l1: 0.321475 + 0.000893084
[620]	cv_agg's l1: 0.3213 + 0.000942058
[621]	cv_agg's l1: 0.32126 + 0.000942246
[622]	cv_agg's l1: 0.321081 + 0.000902746
[623]	cv_agg's l1: 0.320928 + 0.000945562
[62

[805]	cv_agg's l1: 0.302915 + 0.000808089
[806]	cv_agg's l1: 0.302886 + 0.000810253
[807]	cv_agg's l1: 0.302858 + 0.000813963
[808]	cv_agg's l1: 0.30275 + 0.000820615
[809]	cv_agg's l1: 0.302727 + 0.000817907
[810]	cv_agg's l1: 0.302704 + 0.000822754
[811]	cv_agg's l1: 0.302558 + 0.00080326
[812]	cv_agg's l1: 0.30253 + 0.000799732
[813]	cv_agg's l1: 0.302505 + 0.000804474
[814]	cv_agg's l1: 0.302389 + 0.000797517
[815]	cv_agg's l1: 0.302255 + 0.000791969
[816]	cv_agg's l1: 0.302132 + 0.000781936
[817]	cv_agg's l1: 0.302037 + 0.000774318
[818]	cv_agg's l1: 0.301934 + 0.000782719
[819]	cv_agg's l1: 0.301778 + 0.000771435
[820]	cv_agg's l1: 0.30175 + 0.000770721
[821]	cv_agg's l1: 0.301729 + 0.000774078
[822]	cv_agg's l1: 0.301624 + 0.000782161
[823]	cv_agg's l1: 0.301598 + 0.000780159
[824]	cv_agg's l1: 0.301532 + 0.000778789
[825]	cv_agg's l1: 0.301425 + 0.000785762
[826]	cv_agg's l1: 0.301407 + 0.000786741
[827]	cv_agg's l1: 0.301291 + 0.000805253
[828]	cv_agg's l1: 0.301277 + 0.000806

...

[9070]	cv_agg's l1: 0.165819 + 0.00126317
[9071]	cv_agg's l1: 0.165813 + 0.00126332
[9072]	cv_agg's l1: 0.165808 + 0.00126441
[9073]	cv_agg's l1: 0.165801 + 0.00126586
[9074]	cv_agg's l1: 0.1658 + 0.00126528
[9075]	cv_agg's l1: 0.165793 + 0.00126551
[9076]	cv_agg's l1: 0.165785 + 0.00126605
[9077]	cv_agg's l1: 0.165776 + 0.00126491
[9078]	cv_agg's l1: 0.16577 + 0.00126193
[9079]	cv_agg's l1: 0.165769 + 0.00126229
[9080]	cv_agg's l1: 0.165762 + 0.0012621
[9081]	cv_agg's l1: 0.165759 + 0.00125965
[9082]	cv_agg's l1: 0.165757 + 0.00125988
[9083]	cv_agg's l1: 0.165749 + 0.00126046
[9084]	cv_agg's l1: 0.16574 + 0.00126103
[9085]	cv_agg's l1: 0.165739 + 0.00126104
[9086]	cv_agg's l1: 0.165737 + 0.00126186
[9087]	cv_agg's l1: 0.165736 + 0.00126183
[9088]	cv_agg's l1: 0.165731 + 0.00126317
[9089]	cv_agg's l1: 0.16573 + 0.00126314
[9090]	cv_agg's l1: 0.165729 + 0.00126295
[9091]	cv_agg's l1: 0.165724 + 0.00126128
[9092]	cv_agg's l1: 0.165717 + 0.00126141
[9093]	cv_agg's l1: 0.165716 + 0.0012608

[9276]	cv_agg's l1: 0.164798 + 0.00123686
[9277]	cv_agg's l1: 0.164791 + 0.0012386
[9278]	cv_agg's l1: 0.164783 + 0.00123711
[9279]	cv_agg's l1: 0.164774 + 0.00123608
[9280]	cv_agg's l1: 0.164773 + 0.0012355
[9281]	cv_agg's l1: 0.164763 + 0.00123457
[9282]	cv_agg's l1: 0.164762 + 0.00123457
[9283]	cv_agg's l1: 0.164754 + 0.0012357
[9284]	cv_agg's l1: 0.164754 + 0.00123593
[9285]	cv_agg's l1: 0.164746 + 0.00123481
[9286]	cv_agg's l1: 0.164738 + 0.00123356
[9287]	cv_agg's l1: 0.164737 + 0.00123331
[9288]	cv_agg's l1: 0.164732 + 0.00123496
[9289]	cv_agg's l1: 0.16473 + 0.00123483
[9290]	cv_agg's l1: 0.164722 + 0.00123479
[9291]	cv_agg's l1: 0.164711 + 0.00123476
[9292]	cv_agg's l1: 0.164709 + 0.00123495
[9293]	cv_agg's l1: 0.164702 + 0.00123498
[9294]	cv_agg's l1: 0.164696 + 0.00123533
[9295]	cv_agg's l1: 0.164696 + 0.00123574
[9296]	cv_agg's l1: 0.164684 + 0.00123336
[9297]	cv_agg's l1: 0.164676 + 0.00123745
[9298]	cv_agg's l1: 0.164674 + 0.0012372
[9299]	cv_agg's l1: 0.164673 + 0.001236

[9477]	cv_agg's l1: 0.163729 + 0.0012175
[9478]	cv_agg's l1: 0.163721 + 0.00121812
[9479]	cv_agg's l1: 0.163719 + 0.0012187
[9480]	cv_agg's l1: 0.163709 + 0.00121899
[9481]	cv_agg's l1: 0.163703 + 0.00121843
[9482]	cv_agg's l1: 0.163702 + 0.00121736
[9483]	cv_agg's l1: 0.163696 + 0.0012182
[9484]	cv_agg's l1: 0.163695 + 0.00121871
[9485]	cv_agg's l1: 0.163693 + 0.00121871
[9486]	cv_agg's l1: 0.163685 + 0.00121727
[9487]	cv_agg's l1: 0.163679 + 0.0012175
[9488]	cv_agg's l1: 0.163672 + 0.00122003
[9489]	cv_agg's l1: 0.163665 + 0.00122022
[9490]	cv_agg's l1: 0.163659 + 0.00122111
[9491]	cv_agg's l1: 0.16365 + 0.00122389
[9492]	cv_agg's l1: 0.163641 + 0.00122312
[9493]	cv_agg's l1: 0.163633 + 0.00122399
[9494]	cv_agg's l1: 0.163631 + 0.00122468
[9495]	cv_agg's l1: 0.16363 + 0.00122504
[9496]	cv_agg's l1: 0.16363 + 0.00122443
[9497]	cv_agg's l1: 0.163621 + 0.00122466
[9498]	cv_agg's l1: 0.163613 + 0.00122524
[9499]	cv_agg's l1: 0.163612 + 0.00122557
[9500]	cv_agg's l1: 0.163605 + 0.00122764

[9678]	cv_agg's l1: 0.162719 + 0.00123079
[9679]	cv_agg's l1: 0.162718 + 0.00123022
[9680]	cv_agg's l1: 0.162714 + 0.00123048
[9681]	cv_agg's l1: 0.162709 + 0.00123039
[9682]	cv_agg's l1: 0.162701 + 0.00122999
[9683]	cv_agg's l1: 0.162692 + 0.001228
[9684]	cv_agg's l1: 0.162687 + 0.00122936
[9685]	cv_agg's l1: 0.162681 + 0.00123186
[9686]	cv_agg's l1: 0.162675 + 0.00123191
[9687]	cv_agg's l1: 0.162668 + 0.00123077
[9688]	cv_agg's l1: 0.16266 + 0.00122902
[9689]	cv_agg's l1: 0.162655 + 0.00122902
[9690]	cv_agg's l1: 0.162653 + 0.00122948
[9691]	cv_agg's l1: 0.162653 + 0.0012294
[9692]	cv_agg's l1: 0.162646 + 0.0012312
[9693]	cv_agg's l1: 0.162641 + 0.00123242
[9694]	cv_agg's l1: 0.16264 + 0.0012337
[9695]	cv_agg's l1: 0.162636 + 0.00123391
[9696]	cv_agg's l1: 0.162634 + 0.00123355
[9697]	cv_agg's l1: 0.162627 + 0.00123291
[9698]	cv_agg's l1: 0.162625 + 0.00123359
[9699]	cv_agg's l1: 0.162616 + 0.0012357
[9700]	cv_agg's l1: 0.162607 + 0.0012378
[9701]	cv_agg's l1: 0.162606 + 0.0012384
[9

[9881]	cv_agg's l1: 0.161726 + 0.00121281
[9882]	cv_agg's l1: 0.161725 + 0.00121361
[9883]	cv_agg's l1: 0.16172 + 0.00121176
[9884]	cv_agg's l1: 0.161713 + 0.00120957
[9885]	cv_agg's l1: 0.161707 + 0.00121156
[9886]	cv_agg's l1: 0.161702 + 0.00121145
[9887]	cv_agg's l1: 0.161697 + 0.00121146
[9888]	cv_agg's l1: 0.161696 + 0.00121138
[9889]	cv_agg's l1: 0.161691 + 0.00120993
[9890]	cv_agg's l1: 0.161689 + 0.00120918
[9891]	cv_agg's l1: 0.161679 + 0.00121171
[9892]	cv_agg's l1: 0.161673 + 0.00121451
[9893]	cv_agg's l1: 0.161667 + 0.00121391
[9894]	cv_agg's l1: 0.161661 + 0.00121347
[9895]	cv_agg's l1: 0.161651 + 0.00121321
[9896]	cv_agg's l1: 0.161643 + 0.00121108
[9897]	cv_agg's l1: 0.161643 + 0.00121078
[9898]	cv_agg's l1: 0.161641 + 0.00121026
[9899]	cv_agg's l1: 0.161635 + 0.0012082
[9900]	cv_agg's l1: 0.161629 + 0.00120782
[9901]	cv_agg's l1: 0.161628 + 0.00120751
[9902]	cv_agg's l1: 0.161618 + 0.00120608
[9903]	cv_agg's l1: 0.161617 + 0.00120674
[9904]	cv_agg's l1: 0.161616 + 0.001

In [58]:
print(min(result_base['l1-mean']), len(result_base['l1-mean']))

0.16114419962828613 10000


In [59]:
train.shape[0]

92700

In [60]:
test.shape[0]

40559

In [61]:
(100/(train.shape[0]+test.shape[0]))*40559

30.43621819164184

In [62]:
X_train, X_val, y_train, y_val = train_test_split(X, y, test_size=0.304, random_state=42)

In [74]:
n_rounds=20000

In [63]:
lgb_train_2 = lgb.Dataset(X_train, label=y_train, free_raw_data=False)

In [75]:
result_base = lgb.cv(parameters, lgb_train_2, n_rounds, folds=skf.split(X_train, y_train), early_stopping_rounds=10, verbose_eval=1, )

[1]	cv_agg's l1: 0.499548 + 6.15318e-06
[2]	cv_agg's l1: 0.498254 + 6.2626e-05
[3]	cv_agg's l1: 0.496966 + 3.84618e-05
[4]	cv_agg's l1: 0.495684 + 5.34418e-05
[5]	cv_agg's l1: 0.495244 + 5.96505e-05
[6]	cv_agg's l1: 0.494853 + 7.02684e-05
[7]	cv_agg's l1: 0.493603 + 4.04131e-05
[8]	cv_agg's l1: 0.49236 + 5.73942e-05
[9]	cv_agg's l1: 0.49194 + 5.55114e-05
[10]	cv_agg's l1: 0.490662 + 6.80082e-05
[11]	cv_agg's l1: 0.489422 + 9.88715e-05
[12]	cv_agg's l1: 0.488203 + 0.000140508
[13]	cv_agg's l1: 0.48695 + 0.000186582
[14]	cv_agg's l1: 0.486539 + 0.000186427
[15]	cv_agg's l1: 0.485311 + 0.000190564
[16]	cv_agg's l1: 0.484132 + 0.000215223
[17]	cv_agg's l1: 0.483768 + 0.000212817
[18]	cv_agg's l1: 0.482592 + 0.000208825
[19]	cv_agg's l1: 0.481398 + 0.000225675
[20]	cv_agg's l1: 0.481054 + 0.000230728
[21]	cv_agg's l1: 0.479879 + 0.000224863
[22]	cv_agg's l1: 0.479495 + 0.000227967
[23]	cv_agg's l1: 0.479099 + 0.000226057
[24]	cv_agg's l1: 0.478897 + 0.000222018
[25]	cv_agg's l1: 0.477754 + 

[205]	cv_agg's l1: 0.384874 + 0.000922216
[206]	cv_agg's l1: 0.384481 + 0.000951627
[207]	cv_agg's l1: 0.384385 + 0.00095156
[208]	cv_agg's l1: 0.384262 + 0.000951521
[209]	cv_agg's l1: 0.383851 + 0.000909669
[210]	cv_agg's l1: 0.383435 + 0.000920316
[211]	cv_agg's l1: 0.383301 + 0.000923206
[212]	cv_agg's l1: 0.383194 + 0.000924433
[213]	cv_agg's l1: 0.382821 + 0.00096543
[214]	cv_agg's l1: 0.382455 + 0.000995993
[215]	cv_agg's l1: 0.382362 + 0.000994619
[216]	cv_agg's l1: 0.382242 + 0.000998026
[217]	cv_agg's l1: 0.382156 + 0.00100094
[218]	cv_agg's l1: 0.382021 + 0.00100635
[219]	cv_agg's l1: 0.381701 + 0.00103522
[220]	cv_agg's l1: 0.381576 + 0.00103886
[221]	cv_agg's l1: 0.381481 + 0.00104163
[222]	cv_agg's l1: 0.381387 + 0.00104587
[223]	cv_agg's l1: 0.381318 + 0.00104933
[224]	cv_agg's l1: 0.380988 + 0.00106292
[225]	cv_agg's l1: 0.380665 + 0.00106482
[226]	cv_agg's l1: 0.380315 + 0.00102919
[227]	cv_agg's l1: 0.379965 + 0.00100652
[228]	cv_agg's l1: 0.379597 + 0.000985253
[229]

[418]	cv_agg's l1: 0.349598 + 0.00134724
[419]	cv_agg's l1: 0.349542 + 0.00134847
[420]	cv_agg's l1: 0.349482 + 0.00135482
[421]	cv_agg's l1: 0.349303 + 0.00137033
[422]	cv_agg's l1: 0.349084 + 0.00137196
[423]	cv_agg's l1: 0.349029 + 0.00137706
[424]	cv_agg's l1: 0.348969 + 0.00137646
[425]	cv_agg's l1: 0.348909 + 0.00137528
[426]	cv_agg's l1: 0.348862 + 0.00138073
[427]	cv_agg's l1: 0.348726 + 0.00136721
[428]	cv_agg's l1: 0.348581 + 0.00137661
[429]	cv_agg's l1: 0.348371 + 0.00139315
[430]	cv_agg's l1: 0.348327 + 0.0013965
[431]	cv_agg's l1: 0.348273 + 0.00140013
[432]	cv_agg's l1: 0.34804 + 0.00140378
[433]	cv_agg's l1: 0.347899 + 0.00141111
[434]	cv_agg's l1: 0.347837 + 0.00140903
[435]	cv_agg's l1: 0.347677 + 0.0014276
[436]	cv_agg's l1: 0.347528 + 0.0014491
[437]	cv_agg's l1: 0.347486 + 0.0014503
[438]	cv_agg's l1: 0.347262 + 0.0014938
[439]	cv_agg's l1: 0.347166 + 0.00149547
[440]	cv_agg's l1: 0.347113 + 0.00150284
[441]	cv_agg's l1: 0.346956 + 0.00147601
[442]	cv_agg's l1: 0.3

[632]	cv_agg's l1: 0.323772 + 0.00161293
[633]	cv_agg's l1: 0.323734 + 0.00161823
[634]	cv_agg's l1: 0.323564 + 0.00154461
[635]	cv_agg's l1: 0.323474 + 0.00153605
[636]	cv_agg's l1: 0.323377 + 0.00152158
[637]	cv_agg's l1: 0.32321 + 0.00155115
[638]	cv_agg's l1: 0.323059 + 0.00159421
[639]	cv_agg's l1: 0.322891 + 0.00157612
[640]	cv_agg's l1: 0.322732 + 0.00156033
[641]	cv_agg's l1: 0.322652 + 0.00157517
[642]	cv_agg's l1: 0.322625 + 0.00157244
[643]	cv_agg's l1: 0.322585 + 0.00157371
[644]	cv_agg's l1: 0.322547 + 0.00156841
[645]	cv_agg's l1: 0.322352 + 0.00153105
[646]	cv_agg's l1: 0.322324 + 0.00153266
[647]	cv_agg's l1: 0.322215 + 0.00149998
[648]	cv_agg's l1: 0.322091 + 0.00148309
[649]	cv_agg's l1: 0.321926 + 0.00151728
[650]	cv_agg's l1: 0.321769 + 0.00154708
[651]	cv_agg's l1: 0.32163 + 0.00160258
[652]	cv_agg's l1: 0.321481 + 0.0016534
[653]	cv_agg's l1: 0.32129 + 0.00162067
[654]	cv_agg's l1: 0.32111 + 0.00161053
[655]	cv_agg's l1: 0.321083 + 0.00160943
[656]	cv_agg's l1: 0.

[841]	cv_agg's l1: 0.304316 + 0.0014475
[842]	cv_agg's l1: 0.304229 + 0.00142522
[843]	cv_agg's l1: 0.304198 + 0.00141532
[844]	cv_agg's l1: 0.304087 + 0.00143471
[845]	cv_agg's l1: 0.304069 + 0.00143752
[846]	cv_agg's l1: 0.303928 + 0.00142163
[847]	cv_agg's l1: 0.303842 + 0.00145527
[848]	cv_agg's l1: 0.303825 + 0.00145355
[849]	cv_agg's l1: 0.303741 + 0.00146186
[850]	cv_agg's l1: 0.303725 + 0.00146205
[851]	cv_agg's l1: 0.303704 + 0.00146128
[852]	cv_agg's l1: 0.303686 + 0.00146104
[853]	cv_agg's l1: 0.30366 + 0.00146654
[854]	cv_agg's l1: 0.303554 + 0.0014769
[855]	cv_agg's l1: 0.303543 + 0.00147886
[856]	cv_agg's l1: 0.303525 + 0.00147957
[857]	cv_agg's l1: 0.303395 + 0.00150415
[858]	cv_agg's l1: 0.303262 + 0.00152286
[859]	cv_agg's l1: 0.303244 + 0.0015229
[860]	cv_agg's l1: 0.303146 + 0.00158328
[861]	cv_agg's l1: 0.303013 + 0.00153307
[862]	cv_agg's l1: 0.302989 + 0.00153451
[863]	cv_agg's l1: 0.302881 + 0.00152859
[864]	cv_agg's l1: 0.302765 + 0.00153648
[865]	cv_agg's l1: 0

...

[19026]	cv_agg's l1: 0.139076 + 0.00256657
[19027]	cv_agg's l1: 0.139071 + 0.00256488
[19028]	cv_agg's l1: 0.139071 + 0.00256516
[19029]	cv_agg's l1: 0.139068 + 0.00256393
[19030]	cv_agg's l1: 0.139066 + 0.00256288
[19031]	cv_agg's l1: 0.139067 + 0.00256237
[19032]	cv_agg's l1: 0.139066 + 0.00256216
[19033]	cv_agg's l1: 0.139066 + 0.00256181
[19034]	cv_agg's l1: 0.139064 + 0.00256028
[19035]	cv_agg's l1: 0.139062 + 0.00256144
[19036]	cv_agg's l1: 0.139063 + 0.00256161
[19037]	cv_agg's l1: 0.139062 + 0.00256128
[19038]	cv_agg's l1: 0.13906 + 0.00256213
[19039]	cv_agg's l1: 0.139058 + 0.00256324
[19040]	cv_agg's l1: 0.139055 + 0.00256256
[19041]	cv_agg's l1: 0.139055 + 0.00256318
[19042]	cv_agg's l1: 0.139051 + 0.0025632
[19043]	cv_agg's l1: 0.13905 + 0.00256318
[19044]	cv_agg's l1: 0.139046 + 0.00256405
[19045]	cv_agg's l1: 0.139044 + 0.00256355
[19046]	cv_agg's l1: 0.139044 + 0.00256273
[19047]	cv_agg's l1: 0.139044 + 0.00256305
[19048]	cv_agg's l1: 0.139043 + 0.0025634
[19049]	cv_agg'

[19231]	cv_agg's l1: 0.138664 + 0.00256594
[19232]	cv_agg's l1: 0.138664 + 0.00256624
[19233]	cv_agg's l1: 0.138658 + 0.00256544
[19234]	cv_agg's l1: 0.138655 + 0.00256499
[19235]	cv_agg's l1: 0.138652 + 0.00256396
[19236]	cv_agg's l1: 0.138649 + 0.00256293
[19237]	cv_agg's l1: 0.138646 + 0.00256278
[19238]	cv_agg's l1: 0.138641 + 0.00256417
[19239]	cv_agg's l1: 0.138641 + 0.00256489
[19240]	cv_agg's l1: 0.13864 + 0.00256507
[19241]	cv_agg's l1: 0.138636 + 0.00256487
[19242]	cv_agg's l1: 0.138633 + 0.00256441
[19243]	cv_agg's l1: 0.138632 + 0.00256421
[19244]	cv_agg's l1: 0.138631 + 0.00256423
[19245]	cv_agg's l1: 0.138629 + 0.00256386
[19246]	cv_agg's l1: 0.138628 + 0.00256322
[19247]	cv_agg's l1: 0.138627 + 0.00256432
[19248]	cv_agg's l1: 0.138624 + 0.00256648
[19249]	cv_agg's l1: 0.13862 + 0.00256781
[19250]	cv_agg's l1: 0.138619 + 0.00256792
[19251]	cv_agg's l1: 0.138618 + 0.00256866
[19252]	cv_agg's l1: 0.138613 + 0.00256877
[19253]	cv_agg's l1: 0.138613 + 0.00256906
[19254]	cv_ag

[19425]	cv_agg's l1: 0.138319 + 0.00258944
[19426]	cv_agg's l1: 0.138319 + 0.0025886
[19427]	cv_agg's l1: 0.138317 + 0.00258887
[19428]	cv_agg's l1: 0.138316 + 0.00258925
[19429]	cv_agg's l1: 0.138314 + 0.0025893
[19430]	cv_agg's l1: 0.138312 + 0.00259075
[19431]	cv_agg's l1: 0.13831 + 0.00259075
[19432]	cv_agg's l1: 0.138309 + 0.00259058
[19433]	cv_agg's l1: 0.138304 + 0.00259213
[19434]	cv_agg's l1: 0.138299 + 0.0025929
[19435]	cv_agg's l1: 0.138299 + 0.00259311
[19436]	cv_agg's l1: 0.138299 + 0.00259393
[19437]	cv_agg's l1: 0.138298 + 0.00259347
[19438]	cv_agg's l1: 0.138294 + 0.00259243
[19439]	cv_agg's l1: 0.138293 + 0.00259304
[19440]	cv_agg's l1: 0.138293 + 0.00259255
[19441]	cv_agg's l1: 0.138288 + 0.00259201
[19442]	cv_agg's l1: 0.138284 + 0.00259159
[19443]	cv_agg's l1: 0.138282 + 0.0025904
[19444]	cv_agg's l1: 0.138281 + 0.00258981
[19445]	cv_agg's l1: 0.138278 + 0.00258822
[19446]	cv_agg's l1: 0.138274 + 0.00258635
[19447]	cv_agg's l1: 0.138272 + 0.00258696
[19448]	cv_agg's

[19632]	cv_agg's l1: 0.1379 + 0.00256539
[19633]	cv_agg's l1: 0.137896 + 0.00256603
[19634]	cv_agg's l1: 0.137896 + 0.00256685
[19635]	cv_agg's l1: 0.137894 + 0.00256749
[19636]	cv_agg's l1: 0.137891 + 0.00256803
[19637]	cv_agg's l1: 0.13789 + 0.00256811
[19638]	cv_agg's l1: 0.137887 + 0.00256928
[19639]	cv_agg's l1: 0.137885 + 0.00257057
[19640]	cv_agg's l1: 0.137883 + 0.00257122
[19641]	cv_agg's l1: 0.137878 + 0.00257238
[19642]	cv_agg's l1: 0.137874 + 0.00257201
[19643]	cv_agg's l1: 0.137869 + 0.00257324
[19644]	cv_agg's l1: 0.137867 + 0.00257403
[19645]	cv_agg's l1: 0.137864 + 0.00257317
[19646]	cv_agg's l1: 0.137863 + 0.0025735
[19647]	cv_agg's l1: 0.137862 + 0.00257342
[19648]	cv_agg's l1: 0.137862 + 0.00257384
[19649]	cv_agg's l1: 0.137862 + 0.00257392
[19650]	cv_agg's l1: 0.137859 + 0.00257491
[19651]	cv_agg's l1: 0.137855 + 0.002575
[19652]	cv_agg's l1: 0.137855 + 0.00257577
[19653]	cv_agg's l1: 0.13785 + 0.00257431
[19654]	cv_agg's l1: 0.137849 + 0.00257452
[19655]	cv_agg's l

[19836]	cv_agg's l1: 0.137477 + 0.002609
[19837]	cv_agg's l1: 0.137476 + 0.0026093
[19838]	cv_agg's l1: 0.137473 + 0.00260993
[19839]	cv_agg's l1: 0.137471 + 0.00261024
[19840]	cv_agg's l1: 0.137468 + 0.00261238
[19841]	cv_agg's l1: 0.137468 + 0.00261258
[19842]	cv_agg's l1: 0.137464 + 0.00261381
[19843]	cv_agg's l1: 0.137464 + 0.00261349
[19844]	cv_agg's l1: 0.137463 + 0.00261268
[19845]	cv_agg's l1: 0.137463 + 0.00261251
[19846]	cv_agg's l1: 0.13746 + 0.00261213
[19847]	cv_agg's l1: 0.137459 + 0.00261148
[19848]	cv_agg's l1: 0.137455 + 0.00261212
[19849]	cv_agg's l1: 0.137455 + 0.00261232
[19850]	cv_agg's l1: 0.137453 + 0.00261251
[19851]	cv_agg's l1: 0.137453 + 0.0026121
[19852]	cv_agg's l1: 0.137451 + 0.00261165
[19853]	cv_agg's l1: 0.137451 + 0.00261194
[19854]	cv_agg's l1: 0.137446 + 0.00261131
[19855]	cv_agg's l1: 0.137442 + 0.00261206
[19856]	cv_agg's l1: 0.137438 + 0.00261249
[19857]	cv_agg's l1: 0.137438 + 0.00261198
[19858]	cv_agg's l1: 0.137436 + 0.00261362
[19859]	cv_agg's

In [66]:
print(min(result_base['l1-mean']), len(result_base['l1-mean']))

0.16581950741557022 10000


In [76]:
print(min(result_base['l1-mean']), len(result_base['l1-mean']))

0.13717997824168565 20000


In [77]:
#train_data = lgb.Dataset(enc_train, y)
bst = lgb.train(parameters, lgb_train_2,n_rounds)
#test_data = lgb.Dataset(enc_test.drop(['target','is_train'],axis=1))


In [78]:
bst.best_iteration

0

In [79]:
predict_lgb = bst.predict(X_val,num_iteration=bst.best_iteration)

In [72]:
from sklearn.metrics import mean_absolute_error

In [73]:
mean_absolute_error(y_val,predict_lgb)

0.15945249166604453

In [81]:
mean_absolute_error(y_val,predict_lgb)

0.12977580989957122